In [1]:
import pandas as pd
import json
import ast
import numpy as np
from tqdm import tqdm
import time

In [2]:
df_all_data =pd.read_csv("df_all_raw_data.csv")
#drop duplicates of the exact same row
df_all_data = df_all_data.drop_duplicates()
df_all_data.shape

(33367, 13)

### Labeling Season and League

In [3]:
#Create a function which creates the column season (21-22, 22-23, 23-24) and the column League( La Liga, Premier League, ...) based on the column "season_id" of df_all_data :
def add_season_and_league(df, season_league_map):
 
    def get_league(season_id):
        return season_league_map.get(season_id, {}).get('league')

    def get_season(season_id):
        return season_league_map.get(season_id, {}).get('season')

    df['League'] = df['season_id'].apply(get_league)
    df['season'] = df['season_id'].apply(get_season)
    return df

season_league_map = {
    12962: {'league': 'Premier League', 'season': '18-19'},
    16036: {'league': 'Premier League', 'season': '19-20'},
    17420: {'league': 'Premier League', 'season': '20-21'},
    18378: {'league': 'Premier League', 'season': '21-22'},
    19734: {'league': 'Premier League', 'season': '22-23'},
    21646: {'league': 'Premier League', 'season': '23-24'},
    23614: {'league': 'Premier League', 'season': '24-25'},
    13005: {'league': 'Bundesliga', 'season': '18-19'},
    16264: {'league': 'Bundesliga', 'season': '19-20'},
    17361: {'league': 'Bundesliga', 'season': '20-21'},
    18444: {'league': 'Bundesliga', 'season': '21-22'},
    19744: {'league': 'Bundesliga', 'season': '22-23'},
    21795: {'league': 'Bundesliga', 'season': '23-24'},
    23744: {'league': 'Bundesliga', 'season': '24-25'},
    12935: {'league': 'Ligue 1', 'season': '18-19'},
    16043: {'league': 'Ligue 1', 'season': '19-20'},
    17160: {'league': 'Ligue 1', 'season': '20-21'},
    18441: {'league': 'Ligue 1', 'season': '21-22'},
    19745: {'league': 'Ligue 1', 'season': '22-23'},
    21779: {'league': 'Ligue 1', 'season': '23-24'},
    23643: {'league': 'Ligue 1', 'season': '24-25'},
    13158: {'league': 'Serie A', 'season': '18-19'},
    16415: {'league': 'Serie A', 'season': '19-20'},
    17488: {'league': 'Serie A', 'season': '20-21'},
    18576: {'league': 'Serie A', 'season': '21-22'},
    19806: {'league': 'Serie A', 'season': '22-23'},
    21818: {'league': 'Serie A', 'season': '23-24'},
    23746: {'league': 'Serie A', 'season': '24-25'},
    13133: {'league': 'La Liga', 'season': '18-19'},
    16326: {'league': 'La Liga', 'season': '19-20'},
    17480: {'league': 'La Liga', 'season': '20-21'},
    18462: {'league': 'La Liga', 'season': '21-22'},
    19799: {'league': 'La Liga', 'season': '22-23'},
    21694: {'league': 'La Liga', 'season': '23-24'},
    23621: {'league': 'La Liga', 'season': '24-25'},
    13049: {'league': 'Primeira Liga', 'season': '18-19'},
    16346: {'league': 'Primeira Liga', 'season': '19-20'},
    17463: {'league': 'Primeira Liga', 'season': '20-21'},
    18529: {'league': 'Primeira Liga', 'season': '21-22'},
    19896: {'league': 'Primeira Liga', 'season': '22-23'},
    21825: {'league': 'Primeira Liga', 'season': '23-24'},
    23793: {'league': 'Primeira Liga', 'season': '24-25'},
    12946: {'league': 'Eredivisie', 'season': '18-19'},
    16046: {'league': 'Eredivisie', 'season': '19-20'},
    17228: {'league': 'Eredivisie', 'season': '20-21'},
    18350: {'league': 'Eredivisie', 'season': '21-22'},
    19726: {'league': 'Eredivisie', 'season': '22-23'},
    21730: {'league': 'Eredivisie', 'season': '23-24'},
    23628: {'league': 'Eredivisie', 'season': '24-25'},
    12951: {'league': 'Pro League (Belgium)', 'season': '18-19'},
    16276: {'league': 'Pro League (Belgium)', 'season': '19-20'},
    17138: {'league': 'Pro League (Belgium)', 'season': '20-21'},
    18348: {'league': 'Pro League (Belgium)', 'season': '21-22'},
    19785: {'league': 'Pro League (Belgium)', 'season': '22-23'},
    21693: {'league': 'Pro League (Belgium)', 'season': '23-24'},
    23589: {'league': 'Pro League (Belgium)', 'season': '24-25'},
    13251: {'league': 'Serie B', 'season': '18-19'},
    16416: {'league': 'Serie B', 'season': '19-20'},
    17533: {'league': 'Serie B', 'season': '20-21'},
    18710: {'league': 'Serie B', 'season': '21-22'},
    20080: {'league': 'Serie B', 'season': '22-23'},
    21943: {'league': 'Serie B', 'season': '23-24'},
    23839: {'league': 'Serie B', 'season': '24-25'},
    12921: {'league': 'Ekstraklasa (Poland)', 'season': '18-19'},
    16010: {'league': 'Ekstraklasa (Poland)', 'season': '19-20'},
    17287: {'league': 'Ekstraklasa (Poland)', 'season': '20-21'},
    18410: {'league': 'Ekstraklasa (Poland)', 'season': '21-22'},
    19692: {'league': 'Ekstraklasa (Poland)', 'season': '22-23'},
    21650: {'league': 'Ekstraklasa (Poland)', 'season': '23-24'},
    23578: {'league': 'Ekstraklasa (Poland)', 'season': '24-25'},
    13150: {'league': 'La Liga 2', 'season': '18-19'},
    16329: {'league': 'La Liga 2', 'season': '19-20'},
    17483: {'league': 'La Liga 2', 'season': '20-21'},
    18463: {'league': 'La Liga 2', 'season': '21-22'},
    19800: {'league': 'La Liga 2', 'season': '22-23'},
    21739: {'league': 'La Liga 2', 'season': '23-24'},
    23676: {'league': 'La Liga 2', 'season': '24-25'},
    13056: {'league': 'Turkish Süper Lig', 'season': '18-19'},
    16405: {'league': 'Turkish Süper Lig', 'season': '19-20'},
    17449: {'league': 'Turkish Süper Lig', 'season': '20-21'},
    18568: {'league': 'Turkish Süper Lig', 'season': '21-22'},
    19900: {'league': 'Turkish Süper Lig', 'season': '22-23'},
    22057: {'league': 'Turkish Süper Lig', 'season': '23-24'},
    23851: {'league': 'Turkish Süper Lig', 'season': '24-25'},
    13017: {'league': 'Championship (2nd UK)', 'season': '18-19'},
    16211: {'league': 'Championship (2nd UK)', 'season': '19-20'},
    17428: {'league': 'Championship (2nd UK)', 'season': '20-21'},
    18432: {'league': 'Championship (2nd UK)', 'season': '21-22'},
    19793: {'league': 'Championship (2nd UK)', 'season': '22-23'},
    21689: {'league': 'Championship (2nd UK)', 'season': '23-24'},
    23672: {'league': 'Championship (2nd UK)', 'season': '24-25'}
}

df_all_data = add_season_and_league(df_all_data, season_league_map)
df_all_data.sample(5)

fixture_id  season_id  round_id  state_id                 date  \
32756    19172294      23851  343351.0         5  2025-04-19 10:30:00   
2547     10422575      13150  151586.0         5  2019-01-20 15:00:00   
19237    18536915      19745  274934.0         5  2022-08-07 18:45:00   
25245    18842138      21646  307127.0         5  2023-10-28 16:30:00   
24425    18860502      21779  308990.0         5  2023-09-03 13:00:00   

                     home_team         away_team  \
32756                Kasımpaşa         Sivasspor   
2547            Sporting Gijón          Alcorcón   
19237      Olympique Marseille             Reims   
25245  Wolverhampton Wanderers  Newcastle United   
24425                 Le Havre           Lorient   

                                            participants  \
32756  [{'id': 365, 'sport_id': 1, 'country_id': 404,...   
2547   [{'id': 344, 'sport_id': 1, 'country_id': 32, ...   
19237  [{'id': 1028, 'sport_id': 1, 'country_id': 17,...   
25245  [{'id': 29, 'sport_id': 1, 'country_id': 462, ...   
24425  [{'id': 9257, 'sport_id': 1, 'country_id': 17,...   

                                                 lineups  \
32756  [{'id': 14669563646, 'sport_id': 1, 'fixture_i...   
2547   [{'id': 5797044, 'sport_id': 1, 'fixture_id': ...   
19237  [{'id': 32374095, 'sport_id': 1, 'fixture_id':...   
25245  [{'id': 5252069424, 'sport_id': 1, 'fixture_id...   
24425  [{'id': 4606133522, 'sport_id': 1, 'fixture_id...   

                                              formations  \
32756  [{'id': 8449558, 'fixture_id': 19172294, 'part...   
2547   [{'id': 59756, 'fixture_id': 10422575, 'partic...   
19237  [{'id': 337898, 'fixture_id': 18536915, 'parti...   
25245  [{'id': 550099, 'fixture_id': 18842138, 'parti...   
24425  [{'id': 533295, 'fixture_id': 18860502, 'parti...   

                                              statistics  \
32756  [{'id': 362168135, 'fixture_id': 19172294, 'ty...   
2547   [{'id': 3949484, 'fixture_id': 10422575, 'type...   
19237  [{'id': 5579225, 'fixture_id': 18536915, 'type...   
25245  [{'id': 24478215, 'fixture_id': 18842138, 'typ...   
24425  [{'id': 23405366, 'fixture_id': 18860502, 'typ...   

                                                  events  \
32756  [{'id': 149775498, 'fixture_id': 19172294, 'pe...   
2547   [{'id': 32743239, 'fixture_id': 10422575, 'per...   
19237  [{'id': 37657909, 'fixture_id': 18536915, 'per...   
25245  [{'id': 92007748, 'fixture_id': 18842138, 'per...   
24425  [{'id': 90174263, 'fixture_id': 18860502, 'per...   

                                                 weather             League  \
32756  {'id': 587421, 'fixture_id': 19172294, 'venue_...  Turkish Süper Lig   
2547                                                 NaN          La Liga 2   
19237                                                NaN            Ligue 1   
25245  {'id': 312250, 'fixture_id': 18842138, 'venue_...     Premier League   
24425  {'id': 279809, 'fixture_id': 18860502, 'venue_...            Ligue 1   

      season  
32756  24-25  
2547   18-19  
19237  22-23  
25245  23-24  
24425  23-24

## Exctracting Lineup and Bench

In [4]:
import json
import ast

def extract_lineups_and_bench(df):
    
    def process_lineups(lineup_str):

        try:
            lineups = ast.literal_eval(lineup_str)
            
        except json.JSONDecodeError:
            return {"lineup": [], "bench": []}  # Return empty lists if JSON parsing fails

        lineup = []
        bench = []

        for player in lineups:
            
            id_player =  player.get("player_id")
            player_info = {
                id_player : {
                "team_id": player.get("team_id"),
                "position_id": player.get("position_id"),
                "formation_field": player.get("formation_field"),
                "formation_position": player.get("formation_position"),
                "player_name": player.get("player_name"),
                "jersey_number": player.get("jersey_number")
                }
            }
            

            if player.get("type_id") == 11:
                lineup.append(player_info)
            elif player.get("type_id") == 12:
                bench.append(player_info)

        return {"lineup": lineup, "bench": bench}

    result = df["lineups"].apply(process_lineups)
    df["lineup"] = result.apply(lambda x: x["lineup"])
    df["bench"] = result.apply(lambda x: x["bench"])

    return df


df_all_data = extract_lineups_and_bench(df_all_data)
df_all_data.head()

fixture_id  season_id  round_id  state_id                 date  \
0    10329241      12921  168236.0         5  2018-07-20 16:00:00   
1    10329239      12921  168236.0         5  2018-07-20 18:30:00   
2    10329242      12921  168236.0         5  2018-07-21 13:30:00   
3    10329243      12921  168236.0         5  2018-07-21 16:00:00   
4    10329240      12921  168236.0         5  2018-07-21 18:30:00   

               home_team        away_team  \
0          Miedź Legnica   Pogoń Szczecin   
1  Jagiellonia Białystok    Lechia Gdańsk   
2          Śląsk Wrocław  Cracovia Kraków   
3           Wisła Kraków      Arka Gdynia   
4         Legia Warszawa   Zagłębie Lubin   

                                        participants  \
0  [{'id': 244, 'sport_id': 1, 'country_id': 2, '...   
1  [{'id': 890, 'sport_id': 1, 'country_id': 2, '...   
2  [{'id': 3962, 'sport_id': 1, 'country_id': 2, ...   
3  [{'id': 331, 'sport_id': 1, 'country_id': 2, '...   
4  [{'id': 349, 'sport_id': 1, 'country_id': 2, '...   

                                             lineups  \
0  [{'id': 5163775, 'sport_id': 1, 'fixture_id': ...   
1  [{'id': 5164574, 'sport_id': 1, 'fixture_id': ...   
2  [{'id': 5164018, 'sport_id': 1, 'fixture_id': ...   
3  [{'id': 5163837, 'sport_id': 1, 'fixture_id': ...   
4  [{'id': 5164094, 'sport_id': 1, 'fixture_id': ...   

                                          formations  \
0  [{'id': 46276, 'fixture_id': 10329241, 'partic...   
1  [{'id': 46272, 'fixture_id': 10329239, 'partic...   
2  [{'id': 46278, 'fixture_id': 10329242, 'partic...   
3  [{'id': 46280, 'fixture_id': 10329243, 'partic...   
4  [{'id': 46274, 'fixture_id': 10329240, 'partic...   

                                          statistics  \
0  [{'id': 9939831, 'fixture_id': 10329241, 'type...   
1  [{'id': 9765232, 'fixture_id': 10329239, 'type...   
2  [{'id': 9765908, 'fixture_id': 10329242, 'type...   
3  [{'id': 9765341, 'fixture_id': 10329243, 'type...   
4  [{'id': 9764566, 'fixture_id': 10329240, 'type...   

                                              events weather  \
0  [{'id': 32401213, 'fixture_id': 10329241, 'per...     NaN   
1  [{'id': 32401315, 'fixture_id': 10329239, 'per...     NaN   
2  [{'id': 32401294, 'fixture_id': 10329242, 'per...     NaN   
3  [{'id': 32401282, 'fixture_id': 10329243, 'per...     NaN   
4  [{'id': 32401512, 'fixture_id': 10329240, 'per...     NaN   

                 League season  \
0  Ekstraklasa (Poland)  18-19   
1  Ekstraklasa (Poland)  18-19   
2  Ekstraklasa (Poland)  18-19   
3  Ekstraklasa (Poland)  18-19   
4  Ekstraklasa (Poland)  18-19   

                                              lineup  \
0  [{55774: {'team_id': 244, 'position_id': 24, '...   
1  [{155503: {'team_id': 135, 'position_id': 26, ...   
2  [{155547: {'team_id': 1069, 'position_id': 26,...   
3  [{154880: {'team_id': 331, 'position_id': 25, ...   
4  [{76464: {'team_id': 349, 'position_id': 24, '...   

                                               bench  
0  [{155469: {'team_id': 244, 'position_id': 27, ...  
1  [{32271: {'team_id': 135, 'position_id': 24, '...  
2  [{73049: {'team_id': 1069, 'position_id': 26, ...  
3  [{155142: {'team_id': 331, 'position_id': 25, ...  
4  [{72813: {'team_id': 349, 'position_id': 26, '...

In [5]:
df_all_data

fixture_id  season_id  round_id  state_id                 date  \
0        10329241      12921  168236.0         5  2018-07-20 16:00:00   
1        10329239      12921  168236.0         5  2018-07-20 18:30:00   
2        10329242      12921  168236.0         5  2018-07-21 13:30:00   
3        10329243      12921  168236.0         5  2018-07-21 16:00:00   
4        10329240      12921  168236.0         5  2018-07-21 18:30:00   
...           ...        ...       ...       ...                  ...   
33362    19145090      23676  340319.0         1  2025-05-19 18:30:00   
33363    19376848      23839       NaN         1  2025-05-19 18:30:00   
33364    19135032      23614  339272.0         1  2025-05-19 19:00:00   
33365    19135034      23614  339272.0         1  2025-05-20 19:00:00   
33366    19135037      23614  339272.0         1  2025-05-20 19:00:00   

                    home_team                away_team  \
0               Miedź Legnica           Pogoń Szczecin   
1       Jagiellonia Białystok            Lechia Gdańsk   
2               Śląsk Wrocław          Cracovia Kraków   
3                Wisła Kraków              Arka Gdynia   
4              Legia Warszawa           Zagłębie Lubin   
...                       ...                      ...   
33362                 Córdoba                 Mirandés   
33363             17th ranked              16th ranked   
33364  Brighton & Hove Albion                Liverpool   
33365          Crystal Palace  Wolverhampton Wanderers   
33366         Manchester City          AFC Bournemouth   

                                            participants  \
0      [{'id': 244, 'sport_id': 1, 'country_id': 2, '...   
1      [{'id': 890, 'sport_id': 1, 'country_id': 2, '...   
2      [{'id': 3962, 'sport_id': 1, 'country_id': 2, ...   
3      [{'id': 331, 'sport_id': 1, 'country_id': 2, '...   
4      [{'id': 349, 'sport_id': 1, 'country_id': 2, '...   
...                                                  ...   
33362  [{'id': 931, 'sport_id': 1, 'country_id': 32, ...   
33363  [{'id': 267744, 'sport_id': 1, 'country_id': 1...   
33364  [{'id': 78, 'sport_id': 1, 'country_id': 462, ...   
33365  [{'id': 51, 'sport_id': 1, 'country_id': 462, ...   
33366  [{'id': 9, 'sport_id': 1, 'country_id': 462, '...   

                                                 lineups  \
0      [{'id': 5163775, 'sport_id': 1, 'fixture_id': ...   
1      [{'id': 5164574, 'sport_id': 1, 'fixture_id': ...   
2      [{'id': 5164018, 'sport_id': 1, 'fixture_id': ...   
3      [{'id': 5163837, 'sport_id': 1, 'fixture_id': ...   
4      [{'id': 5164094, 'sport_id': 1, 'fixture_id': ...   
...                                                  ...   
33362                                                 []   
33363                                                 []   
33364                                                 []   
33365                                                 []   
33366                                                 []   

                                              formations  \
0      [{'id': 46276, 'fixture_id': 10329241, 'partic...   
1      [{'id': 46272, 'fixture_id': 10329239, 'partic...   
2      [{'id': 46278, 'fixture_id': 10329242, 'partic...   
3      [{'id': 46280, 'fixture_id': 10329243, 'partic...   
4      [{'id': 46274, 'fixture_id': 10329240, 'partic...   
...                                                  ...   
33362                                                 []   
33363                                                 []   
33364                                                 []   
33365                                                 []   
33366                                                 []   

                                              statistics  \
0      [{'id': 9939831, 'fixture_id': 10329241, 'type...   
1      [{'id': 9765232, 'fixture_id': 10329239, 'type...   
2      [{'id': 9765908, 'fixture_id': 10329242, 'type...   
3      [{'id': 9765341, 'fixtu

## Extracting Formations and splitting Local/Away lineup and benches

In [6]:
import ast

# Function to process each row in the DataFrame
def process_row(row):
    # Parse formations from string to list of dictionaries
    formations = ast.literal_eval(row['formations'])
    
    #if formations is empty, return 
    if formations == []:
        return pd.Series({
            'local_lineup': [],
            'away_lineup': [],
            'local_bench': [],
            'away_bench': [],
            'local_formation': None,
            'away_formation': None
        })
    
    # Initialize variables
    local_lineup = []
    away_lineup = []
    local_bench = []
    away_bench = []
    local_formation = None
    away_formation = None
    
    # Variables to store team IDs
    home_team_id = None
    away_team_id = None
    
    # Iterate through formations to separate local and away formations and get team IDs
    for formation in formations:
        if formation['location'] == 'home':
            local_formation = formation['formation']
            home_team_id = formation['participant_id']
    
        elif formation['location'] == 'away':
            away_formation = formation['formation']
            away_team_id = formation['participant_id']
    
    assert home_team_id != away_team_id, f"Home and away team id must be different. Home Team ID: {home_team_id}, Away Team ID: {away_team_id}"
    
    # Create a mapping of team_id to player data
    lineup_dict = {}
    for player in row['lineup']:
        for player_id, player_values in player.items():
            team_id = player_values['team_id']
            if team_id not in lineup_dict:
                lineup_dict[team_id] = []
            player_info = {}
            player_info[player_id] = player_values
            lineup_dict[team_id].append(player_info)


    bench_dict = {}
    for player in row['bench']:
        for player_id, player_values in player.items():
            team_id = player_values['team_id']
            if team_id not in bench_dict:
                bench_dict[team_id] = []
            player_info = {}
            player_info[player_id] = player_values
            bench_dict[team_id].append(player_info)

    # Assign players to local and away lineups based on team IDs
    if home_team_id in lineup_dict:
        local_lineup = lineup_dict[home_team_id]
        # Example logic for assigning bench players (if applicable)
        try:
            local_bench = bench_dict[home_team_id]
        except:
            local_bench = {}


    if away_team_id in lineup_dict:
        away_lineup = lineup_dict[away_team_id]
        # Example logic for assigning bench players (if applicable)
        try:
            away_bench = bench_dict[away_team_id]    
        except:
            away_bench = {}
        
    return pd.Series({
        'local_lineup': local_lineup,
        'away_lineup': away_lineup,
        'local_bench': local_bench,
        'away_bench': away_bench,
        'local_formation': local_formation,
        'away_formation': away_formation
    })

# Apply the function to each row in the DataFrame
df_all_data[['local_lineup', 'away_lineup', 'local_bench', 'away_bench', 'local_formation', 'away_formation']] = df_all_data.apply(process_row, axis=1)

In [7]:
df_all_data

fixture_id  season_id  round_id  state_id                 date  \
0        10329241      12921  168236.0         5  2018-07-20 16:00:00   
1        10329239      12921  168236.0         5  2018-07-20 18:30:00   
2        10329242      12921  168236.0         5  2018-07-21 13:30:00   
3        10329243      12921  168236.0         5  2018-07-21 16:00:00   
4        10329240      12921  168236.0         5  2018-07-21 18:30:00   
...           ...        ...       ...       ...                  ...   
33362    19145090      23676  340319.0         1  2025-05-19 18:30:00   
33363    19376848      23839       NaN         1  2025-05-19 18:30:00   
33364    19135032      23614  339272.0         1  2025-05-19 19:00:00   
33365    19135034      23614  339272.0         1  2025-05-20 19:00:00   
33366    19135037      23614  339272.0         1  2025-05-20 19:00:00   

                    home_team                away_team  \
0               Miedź Legnica           Pogoń Szczecin   
1       Jagiellonia Białystok            Lechia Gdańsk   
2               Śląsk Wrocław          Cracovia Kraków   
3                Wisła Kraków              Arka Gdynia   
4              Legia Warszawa           Zagłębie Lubin   
...                       ...                      ...   
33362                 Córdoba                 Mirandés   
33363             17th ranked              16th ranked   
33364  Brighton & Hove Albion                Liverpool   
33365          Crystal Palace  Wolverhampton Wanderers   
33366         Manchester City          AFC Bournemouth   

                                            participants  \
0      [{'id': 244, 'sport_id': 1, 'country_id': 2, '...   
1      [{'id': 890, 'sport_id': 1, 'country_id': 2, '...   
2      [{'id': 3962, 'sport_id': 1, 'country_id': 2, ...   
3      [{'id': 331, 'sport_id': 1, 'country_id': 2, '...   
4      [{'id': 349, 'sport_id': 1, 'country_id': 2, '...   
...                                                  ...   
33362  [{'id': 931, 'sport_id': 1, 'country_id': 32, ...   
33363  [{'id': 267744, 'sport_id': 1, 'country_id': 1...   
33364  [{'id': 78, 'sport_id': 1, 'country_id': 462, ...   
33365  [{'id': 51, 'sport_id': 1, 'country_id': 462, ...   
33366  [{'id': 9, 'sport_id': 1, 'country_id': 462, '...   

                                                 lineups  \
0      [{'id': 5163775, 'sport_id': 1, 'fixture_id': ...   
1      [{'id': 5164574, 'sport_id': 1, 'fixture_id': ...   
2      [{'id': 5164018, 'sport_id': 1, 'fixture_id': ...   
3      [{'id': 5163837, 'sport_id': 1, 'fixture_id': ...   
4      [{'id': 5164094, 'sport_id': 1, 'fixture_id': ...   
...                                                  ...   
33362                                                 []   
33363                                                 []   
33364                                                 []   
33365                                                 []   
33366                                                 []   

                                              formations  ...  \
0      [{'id': 46276, 'fixture_id': 10329241, 'partic...  ...   
1      [{'id': 46272, 'fixture_id': 10329239, 'partic...  ...   
2      [{'id': 46278, 'fixture_id': 10329242, 'partic...  ...   
3      [{'id': 46280, 'fixture_id': 10329243, 'partic...  ...   
4      [{'id': 46274, 'fixture_id': 10329240, 'partic...  ...   
...                                                  ...  ...   
33362                                                 []  ...   
33363                                                 []  ...   
33364                                                 []  ...   
33365                                                 []  ...   
33366                                                 []  ...   

                     League season  \
0      Ekstraklasa (Poland)  18-19   
1      Ekstraklasa (Poland)  18-19   
2      Ekstraklasa (Poland)  18-19   
3      Ekstraklasa (Poland)  18-19   
4      Ekstraklasa (

## Extracting Round

In [8]:
df_rounds = pd.read_csv("df_rounds.csv")
df_rounds.shape

(3500, 2)

In [9]:
df_rounds

round_id  round_name
0       147706           1
1       147715          10
2       147716          11
3       147717          12
4       147718          13
...        ...         ...
3495    340111           5
3496    340112           6
3497    340113           7
3498    340114           8
3499    340115           9

[3500 rows x 2 columns]

In [10]:
def map_round_id(row):
    filtered_rounds = df_rounds[df_rounds["round_id"] == row["round_id"]]["round_name"]
    if not filtered_rounds.empty:
        row["round"] = filtered_rounds.iloc[0]
    else:
        row["round"] = None  # Or some default value, like "Unknown"
        
    return row
df_all_data = df_all_data.apply(map_round_id, axis=1)

## Drop atypical matches I

In [11]:
#We drop those with no round (knockouts from Eredivisie) and play-outs from Serie A...
df_all_data = df_all_data[~df_all_data["round"].isna()]

## Extracting Statistics

In [12]:
def extract_match_statistics(row):
    # Mapping type_id to relevant stat categories
    stat_map = {
        52: "goals",
        84: "yellow_cards",
        83: "red_cards",
        45: "possession",
        34: "corners"
    }
    
    # Initialize result dictionary
    match_stats = {
        "local_goals": np.NaN, "away_goals":np.NaN,
        "local_yellow_cards": np.NaN, "away_yellow_cards": np.NaN,
        "local_red_cards": np.NaN, "away_red_cards": np.NaN,
        "local_possession": np.NaN, "away_possession": np.NaN,
        "local_corners": np.NaN, "away_corners": np.NaN
    }
    # print("Row variables:", row)
    statistics = ast.literal_eval(row["statistics"]) if isinstance(row["statistics"], str) else row["statistics"]
    # Iterate through statistics data
    for stat in statistics:
        stat_type = stat.get("type_id")
        location = stat.get("location")
        value = stat.get("data", {}).get("value", 0)
        
        if stat_type in stat_map:
            stat_name = stat_map[stat_type]
            key = f"{'local' if location == 'home' else 'away'}_{stat_name}"
            match_stats[key] = value
    for key, value in match_stats.items():
        row[key] = value
        
    return row


df_all_data = df_all_data.apply(extract_match_statistics, axis=1)

In [13]:
df_all_data.head()

fixture_id  season_id  round_id  state_id                 date  \
0    10329241      12921  168236.0         5  2018-07-20 16:00:00   
1    10329239      12921  168236.0         5  2018-07-20 18:30:00   
2    10329242      12921  168236.0         5  2018-07-21 13:30:00   
3    10329243      12921  168236.0         5  2018-07-21 16:00:00   
4    10329240      12921  168236.0         5  2018-07-21 18:30:00   

               home_team        away_team  \
0          Miedź Legnica   Pogoń Szczecin   
1  Jagiellonia Białystok    Lechia Gdańsk   
2          Śląsk Wrocław  Cracovia Kraków   
3           Wisła Kraków      Arka Gdynia   
4         Legia Warszawa   Zagłębie Lubin   

                                        participants  \
0  [{'id': 244, 'sport_id': 1, 'country_id': 2, '...   
1  [{'id': 890, 'sport_id': 1, 'country_id': 2, '...   
2  [{'id': 3962, 'sport_id': 1, 'country_id': 2, ...   
3  [{'id': 331, 'sport_id': 1, 'country_id': 2, '...   
4  [{'id': 349, 'sport_id': 1, 'country_id': 2, '...   

                                             lineups  \
0  [{'id': 5163775, 'sport_id': 1, 'fixture_id': ...   
1  [{'id': 5164574, 'sport_id': 1, 'fixture_id': ...   
2  [{'id': 5164018, 'sport_id': 1, 'fixture_id': ...   
3  [{'id': 5163837, 'sport_id': 1, 'fixture_id': ...   
4  [{'id': 5164094, 'sport_id': 1, 'fixture_id': ...   

                                          formations  ... local_goals  \
0  [{'id': 46276, 'fixture_id': 10329241, 'partic...  ...         1.0   
1  [{'id': 46272, 'fixture_id': 10329239, 'partic...  ...         0.0   
2  [{'id': 46278, 'fixture_id': 10329242, 'partic...  ...         3.0   
3  [{'id': 46280, 'fixture_id': 10329243, 'partic...  ...         0.0   
4  [{'id': 46274, 'fixture_id': 10329240, 'partic...  ...         1.0   

  away_goals local_yellow_cards away_yellow_cards local_red_cards  \
0        0.0                1.0               1.0             0.0   
1        1.0                2.0               5.0             1.0   
2        1.0                1.0               3.0             0.0   
3        0.0                0.0               1.0             0.0   
4        3.0                2.0               1.0             0.0   

  away_red_cards local_possession away_possession local_corners away_corners  
0            0.0             50.0            50.0           3.0          4.0  
1            1.0             52.0            48.0           3.0          2.0  
2            0.0             50.0            50.0           5.0          1.0  
3            0.0             55.0            45.0           7.0          1.0  
4            0.0             61.0            39.0           4.0          5.0  

[5 rows x 34 columns]

## Goals_diff creation (Target Variable)

In [14]:
#Notice that each nan value of each stat means it is 0. (Proved with many matches)
df_all_data[["local_goals", "away_goals", "local_yellow_cards", "away_yellow_cards", 
          "local_red_cards", "away_red_cards"]] = df_all_data[["local_goals", "away_goals", 
                                                            "local_yellow_cards", "away_yellow_cards", 
                                                            "local_red_cards", "away_red_cards"]].fillna(0)
def fill_team_stat(df, col_name, team_side):
    # Determine the team column based on the side
    team_col = "home_team" if team_side == "local" else "away_team"
    
    # Group by season_id and team_col, then calculate the mean for the column
    group_means = df.groupby(["season_id", team_col])[col_name].mean()
    
    # Fill NaN values with the calculated group means
    df[col_name] = df.apply(
        lambda row: group_means.get((row["season_id"], row[team_col]), row[col_name])
        if pd.isna(row[col_name]) else row[col_name], axis=1
    )
    return df

# Apply the function to fill NaN values for the specified columns
for var in ["local_corners", "away_corners", "local_possession", "away_possession"]:
    team_side = var.split("_")[0]  # Extract "local" or "away" from the column name
    df_all_data = fill_team_stat(df_all_data, var, team_side)



In [15]:
df_all_data["local_goals"] = df_all_data["local_goals"].fillna(0)
df_all_data["away_goals"] = df_all_data["away_goals"].fillna(0)

    
df_all_data["goals_diff"] = df_all_data["local_goals"] - df_all_data["away_goals"]

In [16]:
df_all_data[["fixture_id","local_red_cards","away_red_cards","local_yellow_cards","away_yellow_cards",
             "local_goals","away_goals","local_possession","away_possession",
                "local_corners","away_corners","goals_diff"]].to_csv("df_all_data_statistics.csv", index=False)


## Accumulated statistics

In [17]:
# df_stats = df_all_data[["season_id","round","home_team","away_team","local_acc_goals","away_acc_goals","local_acc_yellow_cards","away_acc_yellow_cards","local_acc_red_cards","away_acc_red_cards",
#                        "local_acc_possession","away_acc_possession","local_acc_corners","away_acc_corners"]].copy()
df_all_data[["local_acc_goals","away_acc_goals","local_acc_yellow_cards","away_acc_yellow_cards","local_acc_red_cards","away_acc_red_cards",
                       "local_acc_possession","away_acc_possession","local_acc_corners","away_acc_corners"]] = 0
                    #

df_all_data.loc[df_all_data["round"] == 1.0, [
    "local_acc_goals", "away_acc_goals", "local_acc_yellow_cards", "away_acc_yellow_cards",
    "local_acc_red_cards", "away_acc_red_cards", "local_acc_possession", "away_acc_possession",
    "local_acc_corners", "away_acc_corners"
]] = df_all_data.loc[df_all_data["round"] == 1.0, [
    "local_goals", "away_goals", "local_yellow_cards", "away_yellow_cards",
    "local_red_cards", "away_red_cards", "local_possession", "away_possession",
    "local_corners", "away_corners"
]].values

### Detect cases where there is no data on formations or in statistics or playoffs + knockouts 

In [18]:
df_all_data[((df_all_data["formations"] == "[]") | (df_all_data["statistics"] == "[]")) & (df_all_data["season"] != "24-25") ][["season_id","League","season"]].value_counts()

season_id  League                 season
16043      Ligue 1                19-20     101
16046      Eredivisie             19-20      74
12951      Pro League (Belgium)   18-19      47
19900      Turkish Süper Lig      22-23      29
13150      La Liga 2              18-19      21
16276      Pro League (Belgium)   19-20       9
13017      Championship (2nd UK)  18-19       1
17533      Serie B                20-21       1
21693      Pro League (Belgium)   23-24       1
Name: count, dtype: int64

In [19]:
#-------------18-19,  19-20, 20-21, 21-22, 22-23, 23-24, 24-25
season_list = [                                                  #Pro League (Belgium)
                                    18710, 20080, 21943, 23839,  #Serie B
                             17287, 18410, 19692, 21650, 23578,  #Ekstraklasa (Poland) 
                      16329, 17483, 18463, 19800, 21739, 23676, #La Liga 2
               13056, 16405,        18568       , 22057,        #Turkish Süper Lig
                      16211, 17428, 18432, 19793, 21689, 23672, #Championship (2nd UK)
                      
               12962, 16036, 17420, 18378, 19734, 21646, 23614, # Premier League
               13005, 16264, 17361, 18444, 19744, 21795, 23744,  # Bundesliga
               12935       , 17160, 18441, 19745, 21779, 23643, # Ligue 1
               13158, 16415, 17488, 18576, 19806, 21818, 23746,  # Serie A
               13133, 16326, 17480, 18462, 19799, 21694, 23621,  # La Liga
               13049, 16346, 17463, 18529, 19896, 21825, 23793,   # Primeira Liga
               12946       , 17228, 18350, 19726, 21730, 23628  # Eredivisie

               
               
 ]

#We delete the 24-25 Turkish Süper League and 18-19 Serie B as it has 19 teams and is more difficult to get the stats
#We delete the 20-21 Turkish Süper League as it has 21 teams and is more difficult to get the stats
#We delete also others seasons with nan values:



df_all_data = df_all_data[df_all_data["season_id"].isin(season_list)]

In [20]:
#Delete the most recent dates (just keep the newest one)  where for a given "season_id", "round" and ("home_team" or "away_team") there are more than 1 match
#First order by date
df_all_data = df_all_data.sort_values(by=["date"], ascending=True)
print(len(df_all_data))
#Then drop duplicates
df_all_data = df_all_data.drop_duplicates(subset=["season_id", "round", "home_team"], keep="first")
df_all_data = df_all_data.drop_duplicates(subset=["season_id", "round", "away_team"], keep="first")
print(len(df_all_data))
#We have dropped the rounds of some play-offs and knockouts

26611
26611


### Analyze the NANS before computing the acc variables

In [21]:
df_all_data.isna().sum()

fixture_id                    0
season_id                     0
round_id                      0
state_id                      0
date                          0
home_team                     0
away_team                     0
participants                  0
lineups                       0
formations                    0
statistics                    0
events                        0
weather                   10632
League                        0
season                        0
lineup                        0
bench                         0
local_lineup                  0
away_lineup                   0
local_bench                   0
away_bench                    0
local_formation              85
away_formation               85
round                         0
local_goals                   0
away_goals                    0
local_yellow_cards            0
away_yellow_cards             0
local_red_cards               0
away_red_cards                0
local_possession              0
away_pos

## Create target variable

In [22]:
def map_winner(row):
    if row["local_goals"] > row["away_goals"]:
        row["winner"] = 1
    elif row["local_goals"] < row["away_goals"]:
        row["winner"] = -1
    else: # draw case
        row["winner"] = 0
    return row


df_all_data = df_all_data.apply(map_winner, axis=1)

In [23]:

# local_stats_columns = ["local_goals","local_yellow_cards","local_red_cards","local_possession","local_corners"]
# away_stats_columns = ["away_goals","away_yellow_cards","away_red_cards","away_possession","away_corners"]
stats_columns = ["goals","yellow_cards","red_cards","possession","corners"]


#Just considered leagues with at least 16 teams. 

for col in stats_columns:
    for season in tqdm(season_list):
        teams_list = df_all_data.loc[(df_all_data['season_id'] == season), 'home_team'].unique().tolist()
        for team in teams_list:
            last_stat = 0
            
            for round_aux in range(1,int(df_all_data.loc[df_all_data["season_id"] == season, "round"].unique().max())+1):
                round  = float(round_aux)
            
                
                eslocal = len(df_all_data.loc[(df_all_data['season_id'] == season) & (df_all_data['round'] == round) & 
                                                (df_all_data['home_team'] == team)])  #1 if its local
                if round_aux != 1:
                    
                    eralocal = len(df_all_data.loc[(df_all_data['season_id'] == season) & (df_all_data['round'] == round-1) & 
                                                (df_all_data['home_team'] == team)])  #1 if it was local in the previous round
                    
                    
                    if eslocal == 1 and eralocal == 1:
                        stats_name = f"local_acc_{col}"
                        old_stats_name = stats_name
                        old_stats_name_abs = f"local_{col}"
                        df_all_data.loc[(df_all_data["season_id"] == season)  & (df_all_data["round"]==round) & (df_all_data["home_team"]==team), stats_name] = \
                        (last_stat + df_all_data.loc[(df_all_data["season_id"] == season) & (df_all_data["round"]==round - 1) & (df_all_data["home_team"]==team), old_stats_name].iloc[0]) /(round_aux-1) 
                        
                        last_stat +=  df_all_data.loc[(df_all_data["season_id"] == season) & (df_all_data["round"]==round - 1) & (df_all_data["home_team"]==team), old_stats_name_abs].iloc[0]
                        #The mean of each stat is computed, so there is no difference while comparing with other leagues with less rounds.
            
                    elif eslocal == 1 and eralocal == 0:
                        stats_name = f"local_acc_{col}"
                        old_stats_name = f"away_acc_{col}" 
                        old_stats_name_abs = f"away_{col}"

                        if not df_all_data.loc[(df_all_data["season_id"] == season) & (df_all_data["round"] == round - 1) & (df_all_data["away_team"] == team), old_stats_name].empty:
                            df_all_data.loc[(df_all_data["season_id"] == season) & (df_all_data["round"] == round) & (df_all_data["home_team"] == team), stats_name] = \
                            (last_stat + df_all_data.loc[(df_all_data["season_id"] == season) & (df_all_data["round"] == round - 1) & (df_all_data["away_team"] == team), old_stats_name].iloc[0]) / (round_aux - 1)
                            last_stat += df_all_data.loc[(df_all_data["season_id"] == season) & (df_all_data["round"] == round - 1) & (df_all_data["away_team"] == team), old_stats_name_abs].iloc[0]
                        else:
                            raise IndexError(f"Data not found for season: {season}, round: {round}, team: {team}, stats_name: {stats_name}")
            
                    elif eslocal == 0 and eralocal == 1:
                        stats_name = f"away_acc_{col}"
                        old_stats_name = f"local_acc_{col}"
                        old_stats_name_abs = f"local_{col}"

                        df_all_data.loc[(df_all_data["season_id"] == season)  & (df_all_data["round"]==round) & (df_all_data["away_team"]==team), stats_name] = \
                        (last_stat + df_all_data.loc[(df_all_data["season_id"] == season) & (df_all_data["round"]==round - 1) & (df_all_data["home_team"]==team), old_stats_name].iloc[0]) /(round_aux-1)  
                        last_stat += df_all_data.loc[(df_all_data["season_id"] == season) & (df_all_data["round"]==round - 1) & (df_all_data["home_team"]==team), old_stats_name_abs].iloc[0]
            
                    elif eslocal == 0 and eralocal == 0:
                        stats_name = f"away_acc_{col}"
                        old_stats_name = stats_name
                        old_stats_name_abs = f"away_{col}"

                        if not df_all_data.loc[(df_all_data["season_id"] == season) & (df_all_data["round"] == round - 1) & (df_all_data["away_team"] == team), old_stats_name].empty:
                            df_all_data.loc[(df_all_data["season_id"] == season)  & (df_all_data["round"]==round) & (df_all_data["away_team"]==team), stats_name] = \
                            (last_stat + df_all_data.loc[(df_all_data["season_id"] == season) & (df_all_data["round"]==round - 1) & (df_all_data["away_team"]==team), old_stats_name].iloc[0] ) /(round_aux-1)
                            last_stat  += df_all_data.loc[(df_all_data["season_id"] == season) & (df_all_data["round"]==round - 1) & (df_all_data["away_team"]==team), old_stats_name_abs].iloc[0] 
                            
                        else:
                            raise IndexError(f"Data not found for season: {season}, round: {round}, team: {team}, stats_name: {stats_name}") 
                    
                    else:
                        df_all_data[(df_all_data['season_id'] == season) & (df_all_data['round'] == round) & 
                                                (df_all_data['home_team'] == team)].head()
                        raise ValueError(f"Unexpected case encountered for team: {team} at season: {season} and round: {round_aux}\n eslocal: {eslocal}, eralocal: {eralocal}")


df_all_data.tail()

  0%|          | 0/72 [00:00<?, ?it/s]C:\Users\genis\AppData\Local\Temp\ipykernel_49816\2383394891.py:42: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise in a future error of pandas. Value '1.5' has dtype incompatible with int64, please explicitly cast to a compatible dtype first.
  df_all_data.loc[(df_all_data["season_id"] == season) & (df_all_data["round"] == round) & (df_all_data["home_team"] == team), stats_name] = \
C:\Users\genis\AppData\Local\Temp\ipykernel_49816\2383394891.py:53: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise in a future error of pandas. Value '1.5' has dtype incompatible with int64, please explicitly cast to a compatible dtype first.
  df_all_data.loc[(df_all_data["season_id"] == season)  & (df_all_data["round"]==round) & (df_all_data["away_team"]==team), stats_name] = \
  0%|          | 0/72 [00:00<?, ?it/s]C:\Users\genis\AppData\Local\Temp\ipykernel_49816\2383394891.py:53: FutureWarning: Se

fixture_id  season_id  round_id  state_id                 date  \
33361    19129777      23578  338720.0         1  2025-05-19 17:00:00   
33362    19145090      23676  340319.0         1  2025-05-19 18:30:00   
33364    19135032      23614  339272.0         1  2025-05-19 19:00:00   
33365    19135034      23614  339272.0         1  2025-05-20 19:00:00   
33366    19135037      23614  339272.0         1  2025-05-20 19:00:00   

                    home_team                away_team  \
33361             Widzew Lodz      Puszcza Niepołomice   
33362                 Córdoba                 Mirandés   
33364  Brighton & Hove Albion                Liverpool   
33365          Crystal Palace  Wolverhampton Wanderers   
33366         Manchester City          AFC Bournemouth   

                                            participants lineups formations  \
33361  [{'id': 8761, 'sport_id': 1, 'country_id': 2, ...      []         []   
33362  [{'id': 931, 'sport_id': 1, 'country_id': 32, ...      []         []   
33364  [{'id': 78, 'sport_id': 1, 'country_id': 462, ...      []         []   
33365  [{'id': 51, 'sport_id': 1, 'country_id': 462, ...      []         []   
33366  [{'id': 9, 'sport_id': 1, 'country_id': 462, '...      []         []   

       ... away_acc_goals local_acc_yellow_cards away_acc_yellow_cards  \
33361  ...       1.096773               2.098967              2.550993   
33362  ...       1.342330               3.185747              2.264002   
33364  ...       2.315297               2.200168              1.828427   
33365  ...       1.458298               2.227968              2.116041   
33366  ...       1.571093               1.658467              2.571860   

      local_acc_red_cards away_acc_red_cards local_acc_possession  \
33361            0.161464           0.129137            48.914541   
33362            0.184323           0.131673            55.465468   
33364            0.085786           0.057191            52.491004   
33365            0.114381           0.057191            42.938155   
33366            0.028596           0.057167            61.569452   

      away_acc_possession local_acc_corners away_acc_corners winner  
33361           39.393032          4.352061         3.932389      0  
33362           45.438517          5.812918         4.525978      0  
33364           58.194348          4.860220         6.714834      0  
33365           47.237548          4.655194         3.541656      0  
33366           47.827014          6.544855         6.031074      0  

[5 rows x 46 columns]

In [24]:
#Reinitialize the first rounds
df_all_data.loc[df_all_data["round"] == 1.0, ["local_acc_goals","away_acc_goals","local_acc_yellow_cards","away_acc_yellow_cards","local_acc_red_cards","away_acc_red_cards",
                       "local_acc_possession","away_acc_possession","local_acc_corners","away_acc_corners"]] = 0

In [25]:
df_all_data[(df_all_data["season_id"] == 17449) & (df_all_data["round"] == 8.0)]

Empty DataFrame
Columns: [fixture_id, season_id, round_id, state_id, date, home_team, away_team, participants, lineups, formations, statistics, events, weather, League, season, lineup, bench, local_lineup, away_lineup, local_bench, away_bench, local_formation, away_formation, round, local_goals, away_goals, local_yellow_cards, away_yellow_cards, local_red_cards, away_red_cards, local_possession, away_possession, local_corners, away_corners, goals_diff, local_acc_goals, away_acc_goals, local_acc_yellow_cards, away_acc_yellow_cards, local_acc_red_cards, away_acc_red_cards, local_acc_possession, away_acc_possession, local_acc_corners, away_acc_corners, winner]
Index: []

[0 rows x 46 columns]

In [26]:
(df_all_data.groupby("season_id")["home_team"].nunique() == 15).loc[lambda x: x]

Series([], Name: home_team, dtype: bool)

There are still some stats variables with 0 which must not be 0, such as corners or possession. These cases are just round=1, so there will be removed later.

## Extracting Weather Information

In [27]:
df_all_data[df_all_data["fixture_id"]==18165999]["weather"].iloc[0]

"{'id': 92176, 'fixture_id': 18165999, 'venue_id': 2020, 'temperature': {'day': 10.9, 'morning': 8.75, 'evening': 11.38, 'night': 10.59}, 'feels_like': {'day': 9.64, 'morning': 7.16, 'evening': 10.3, 'night': 9.58}, 'wind': {'speed': 7.07, 'direction': 129}, 'humidity': '61%', 'pressure': 1021, 'clouds': '100%', 'description': 'overcast clouds', 'icon': 'https://cdn.sportmonks.com/images/weather/04d.png', 'type': 'actual', 'metric': 'celcius', 'current': None}"

In [28]:
import pandas as pd
import ast

def extract_weather(row):
    """
    Extracts weather details from a given row.

    Parameters:
    - row (pd.Series): A row of the DataFrame containing match data.

    Returns:
    - pd.Series: The modified row with extracted weather information.
    """
    # Extract weather dictionary (convert from string if necessary)
    weather_data = row["weather"]

    if isinstance(weather_data, str):
        weather_data = ast.literal_eval(weather_data)

    if not isinstance(weather_data, dict):
        return row  # Return unchanged if weather data is not in the expected format

    # Extract match time and determine time of day
    match_time = pd.to_datetime(row["date"])  

    if 6 <= match_time.hour < 12:
        time_of_day = "morning"
    elif 12 <= match_time.hour < 18:
        time_of_day = "day"
    elif 18 <= match_time.hour < 20:
        time_of_day = "evening"
    else:
        time_of_day = "night"

    # Extract temperature safely
    temperature_data = weather_data.get("temperature", {})
    feels_like_data = weather_data.get("feels_like", {})

    if not isinstance(temperature_data, dict) or not isinstance(feels_like_data, dict):
        return row  # If these are not dictionaries, return the row unchanged

    temperature = temperature_data.get(time_of_day, None)
    feels_like = feels_like_data.get(time_of_day, None)

    # Extract other weather details
    wind_speed = weather_data.get("wind", {}).get("speed", None)
    humidity = weather_data.get("humidity", "").replace("%", "")
    clouds = weather_data.get("clouds", "").replace("%", "")

    try:
        humidity = int(humidity) if humidity else None
    except ValueError:
        humidity = None

    try:
        clouds = int(clouds) if clouds else None
    except ValueError:
        clouds = None

    # Convert temperature if necessary
    metric = weather_data.get("metric", "celsius").lower()

    if metric == "fahrenheit":
        temperature = (temperature - 32) * 5 / 9 if temperature is not None else None
        feels_like = (feels_like - 32) * 5 / 9 if feels_like is not None else None
    elif metric == "kelvin":
        temperature = temperature - 273.15 if temperature is not None else None
        feels_like = feels_like - 273.15 if feels_like is not None else None

    # print(type(row))
    # Assign new values        
    row["wind_speed"] = wind_speed
    row["humidity"] = humidity
    row["temperature"] = np.round(temperature, 2) if temperature is not None else None
    row["feels_like"] = np.round(feels_like, 2) if feels_like is not None else None
    row["clouds"] = clouds

    return row

# Apply function to DataFrame
df_all_data = df_all_data.apply(extract_weather, axis = 1)


In [29]:
df_all_data

League  away_acc_corners  away_acc_goals  \
55               Eredivisie          0.000000        0.000000   
58                  Ligue 1          0.000000        0.000000   
59        Turkish Süper Lig          0.000000        0.000000   
60           Premier League          0.000000        0.000000   
61            Primeira Liga          0.000000        0.000000   
...                     ...               ...             ...   
33361  Ekstraklasa (Poland)          3.932389        1.096773   
33362             La Liga 2          4.525978        1.342330   
33364        Premier League          6.714834        2.315297   
33365        Premier League          3.541656        1.458298   
33366        Premier League          6.031074        1.571093   

       away_acc_possession  away_acc_red_cards  away_acc_yellow_cards  \
55                0.000000            0.000000               0.000000   
58                0.000000            0.000000               0.000000   
59                0.000000            0.000000               0.000000   
60                0.000000            0.000000               0.000000   
61                0.000000            0.000000               0.000000   
...                    ...                 ...                    ...   
33361            39.393032            0.129137               2.550993   
33362            45.438517            0.131673               2.264002   
33364            58.194348            0.057191               1.828427   
33365            47.237548            0.057191               2.116041   
33366            47.827014            0.057167               2.571860   

                                              away_bench  away_corners  \
55     [{150982: {'team_id': 1053, 'position_id': 25,...      1.000000   
58     [{96587: {'team_id': 289, 'position_id': 24, '...      1.000000   
59     [{201416: {'team_id': 34, 'position_id': 25, '...      4.000000   
60     [{612: {'team_id': 42, 'position_id': 25, 'for...      5.000000   
61     [{161798: {'team_id': 830, 'position_id': 27, ...      2.000000   
...                                                  ...           ...   
33361                                                 []      3.875000   
33362                                                 []      4.263158   
33364                                                 []      7.000000   
33365                                                 []      3.611111   
33366                                                 []      6.000000   

      away_formation  away_goals  ... round  round_id  season season_id  \
55             4-3-3         3.0  ...   1.0  147497.0   18-19     12946   
58           4-2-3-1         0.0  ...   1.0  147225.0   18-19     12935   
59           4-2-3-1         3.0  ...   1.0  149836.0   18-19     13056   
60           4-2-3-1         1.0  ...   1.0  147706.0   18-19     12962   
61           4-2-3-1         2.0  ...   1.0  149559.0   18-19     13049   
...              ...         ...  ...   ...       ...     ...       ...   
33361           None         0.0  ...  33.0  338720.0   24-25     23578   
33362           None         0.0  ...  40.0  340319.0   24-25     23676   
33364           None         0.0  ...  37.0  339272.0   24-25     23614   
33365           None         0.0  ...  37.0  339272.0   24-25     23614   
33366           None         0.0  ...  37.0  339272.0   24-25     23614   

       state_id                                         statistics  \
55            5  [{'id': 9999693, 'fixture_id': 10331747, 'type...   
58            5  [{'id': 9914215, 'fixture_id': 10330193, 'type...   
59            5  [{'id': 10074152, 'fixture_id': 10353716, 'typ...   
60            5  [{'id': 9758459, 'fixture_id': 10332766, 'type...   
61            5  [{'id': 9900505, 'fixture_id': 10350714, 'type...   
...         ...                                                ...   
33361         1                                                 []   
33362        

In [30]:
df_all_data

League  away_acc_corners  away_acc_goals  \
55               Eredivisie          0.000000        0.000000   
58                  Ligue 1          0.000000        0.000000   
59        Turkish Süper Lig          0.000000        0.000000   
60           Premier League          0.000000        0.000000   
61            Primeira Liga          0.000000        0.000000   
...                     ...               ...             ...   
33361  Ekstraklasa (Poland)          3.932389        1.096773   
33362             La Liga 2          4.525978        1.342330   
33364        Premier League          6.714834        2.315297   
33365        Premier League          3.541656        1.458298   
33366        Premier League          6.031074        1.571093   

       away_acc_possession  away_acc_red_cards  away_acc_yellow_cards  \
55                0.000000            0.000000               0.000000   
58                0.000000            0.000000               0.000000   
59                0.000000            0.000000               0.000000   
60                0.000000            0.000000               0.000000   
61                0.000000            0.000000               0.000000   
...                    ...                 ...                    ...   
33361            39.393032            0.129137               2.550993   
33362            45.438517            0.131673               2.264002   
33364            58.194348            0.057191               1.828427   
33365            47.237548            0.057191               2.116041   
33366            47.827014            0.057167               2.571860   

                                              away_bench  away_corners  \
55     [{150982: {'team_id': 1053, 'position_id': 25,...      1.000000   
58     [{96587: {'team_id': 289, 'position_id': 24, '...      1.000000   
59     [{201416: {'team_id': 34, 'position_id': 25, '...      4.000000   
60     [{612: {'team_id': 42, 'position_id': 25, 'for...      5.000000   
61     [{161798: {'team_id': 830, 'position_id': 27, ...      2.000000   
...                                                  ...           ...   
33361                                                 []      3.875000   
33362                                                 []      4.263158   
33364                                                 []      7.000000   
33365                                                 []      3.611111   
33366                                                 []      6.000000   

      away_formation  away_goals  ... round  round_id  season season_id  \
55             4-3-3         3.0  ...   1.0  147497.0   18-19     12946   
58           4-2-3-1         0.0  ...   1.0  147225.0   18-19     12935   
59           4-2-3-1         3.0  ...   1.0  149836.0   18-19     13056   
60           4-2-3-1         1.0  ...   1.0  147706.0   18-19     12962   
61           4-2-3-1         2.0  ...   1.0  149559.0   18-19     13049   
...              ...         ...  ...   ...       ...     ...       ...   
33361           None         0.0  ...  33.0  338720.0   24-25     23578   
33362           None         0.0  ...  40.0  340319.0   24-25     23676   
33364           None         0.0  ...  37.0  339272.0   24-25     23614   
33365           None         0.0  ...  37.0  339272.0   24-25     23614   
33366           None         0.0  ...  37.0  339272.0   24-25     23614   

       state_id                                         statistics  \
55            5  [{'id': 9999693, 'fixture_id': 10331747, 'type...   
58            5  [{'id': 9914215, 'fixture_id': 10330193, 'type...   
59            5  [{'id': 10074152, 'fixture_id': 10353716, 'typ...   
60            5  [{'id': 9758459, 'fixture_id': 10332766, 'type...   
61            5  [{'id': 9900505, 'fixture_id': 10350714, 'type...   
...         ...                                                ...   
33361         1                                                 []   
33362        

In [31]:
def map_points(row):
    
    if row["winner"]==1:
        row["local_acc_points"] += 3
        row["local_acc_points"] += 0

    elif row["winner"]==-1:
        row["local_acc_points"] += 0
        row["away_acc_points"] += 3
    else:
        row["local_acc_points"] += 1
        row["away_acc_points"] += 1
        
    return row



In [32]:
df_all_data[(df_all_data["round"]==38) & (df_all_data["League"]== "La Liga") & (df_all_data["season_id"]==21694)][["home_team","away_team","local_acc_goals","away_acc_goals","local_acc_yellow_cards","away_acc_yellow_cards","local_acc_red_cards","away_acc_red_cards","local_acc_corners","away_acc_corners","local_acc_possession","away_acc_possession","goals_diff"]]

home_team         away_team  local_acc_goals  away_acc_goals  \
28650          Girona           Granada         2.084944        1.027823   
28651         Osasuna        Villarreal         1.111178        1.667152   
28653   Real Sociedad   Atlético Madrid         1.361420        1.860250   
28665  Rayo Vallecano     Athletic Club         0.804651        1.611575   
28666         Almería             Cádiz         0.972951        0.694202   
28672     Real Madrid        Real Betis         2.303435        1.332781   
28673          Getafe          Mallorca         1.139795        0.805402   
28675   Celta de Vigo          Valencia         1.166047        1.028595   
28676      Las Palmas  Deportivo Alavés         0.888050        0.945151   
28705         Sevilla      FC Barcelona         1.306548        2.055600   

       local_acc_yellow_cards  away_acc_yellow_cards  local_acc_red_cards  \
28650                1.861775               2.444025             0.027800   
28651                1.862503               2.749052             0.138999   
28653                2.446322               2.193850             0.055600   
28665                2.749050               2.001546             0.138227   
28666                2.279544               2.806131             0.138999   
28672                1.750619               2.251016             0.083400   
28673                3.305050               2.640082             0.194599   
28675                1.694222               1.666424             0.111200   
28676                2.111200               2.111950             0.111200   
28705                2.858638               2.250971             0.111200   

       away_acc_red_cards  local_acc_corners  away_acc_corners  \
28650            0.083400           4.193848          3.803767   
28651            0.193826           4.418497          4.641585   
28653            0.111200           5.224010          4.528972   
28665            0.138998           4.332072          5.529676   
28666            0.166799           4.555977          4.468689   
28672            0.083400           5.667969          5.720523   
28673            0.055600           3.859495          4.361441   
28675            0.138999           4.918877          3.250131   
28676            0.027800           4.278044          4.975290   
28705            0.055600           4.752981          6.277227   

       local_acc_possession  away_acc_possession  goals_diff  
28650             56.631481            45.843318         7.0  
28651             47.635846            49.622971         0.0  
28653             56.248170            50.774406        -2.0  
28665             49.542074            50.113151        -1.0  
28666             46.091755            42.471767         5.0  
28672             59.295766            50.339069         0.0  
28673             44.527169            44.413897        -1.0  
28675             45.855629            44.029978         0.0  
28676             59.780016            41.510576         0.0  
28705             50.745379            64.527582        -1.0

## Create team strength variables

In [33]:
from tqdm import tqdm

for season in tqdm(tqdm(df_all_data["season_id"].unique())):
# for season in [21694]:
    df_all_data.loc[(df_all_data['season'] == season), 'local_acc_pointsL'] = 0
    df_all_data.loc[(df_all_data['season'] == season), 'local_acc_pointsA'] = 0
    df_all_data.loc[(df_all_data['season'] == season), 'away_acc_pointsL'] = 0  
    df_all_data.loc[(df_all_data['season'] == season), 'away_acc_pointsA'] = 0
    df_all_data.loc[(df_all_data['season'] == season), 'local_acc_points'] = 0
    df_all_data.loc[(df_all_data['season'] == season), 'away_acc_points'] = 0
    #fem llista d'equips d'aquella season:
    teams_list = df_all_data.loc[(df_all_data['season_id'] == season), 'home_team'].unique().tolist()
    #print(teams_list)
    
    
    for team in teams_list:
        counter_points_local = 0
        counter_points_visitor = 0
        counter_partits_local = 1 #evitem error partit 0
        counter_partits_visitor = 1
        entrada_local = False
        entrada_visitor = False
        total_counter_points = 0
        # print(team)
        for round_aux in range(1,int(df_all_data.loc[df_all_data["season_id"] == season, "round"].unique().max())+1):
            round = float(round_aux)
            #comptem els punts d'aquella ronda de l'team que estem iterant i els sumem a PliS si és local i a PviS si és visitant
            result_aux_df = df_all_data.loc[(df_all_data['season_id'] == season) & (df_all_data['round'] == round) & 
                                       ((df_all_data['home_team'] == team) | (df_all_data['away_team']== team)), 'winner']
            
            # print(result_aux_df)
            # print("counter points",total_counter_points)
            if not result_aux_df.empty and len(result_aux_df)==1:
                result_aux = result_aux_df.iloc[0]            #result_aux és el resultat de l'team local
                # print("result winner",result_aux,"at round",round)
                #calculem si l'equip és local o visitant
                eslocal = len(df_all_data.loc[(df_all_data['season_id'] == season) & (df_all_data['round'] == round) & 
                                        (df_all_data['home_team'] == team)])
                #eslocal --> 1 si és local, 0 si és visitant
                # print("Es local?",eslocal)
                if eslocal > 1: 
                    raise Exception('Error: hi ha més d\'un partit de l\'equip com a local en una mateixa jornada')
                elif eslocal == 1:
                    # print(counter_partits_local)

                    #desem els punts a PliS abans d'actualitzar el counter_points:
                    df_all_data.loc[(df_all_data['season_id'] == season) & (df_all_data['round'] == round) & 
                                        (df_all_data['home_team'] == team), 'local_acc_pointsL'] = counter_points_local/(3*counter_partits_local)
                    df_all_data.loc[(df_all_data['season_id'] == season) & (df_all_data['round'] == round) &
                                            (df_all_data['home_team'] == team), 'local_acc_pointsA'] = counter_points_visitor/(3*counter_partits_visitor) #no incrementem el counter
                    
                    df_all_data.loc[(df_all_data['season_id'] == season) & (df_all_data['round'] == round) &
                                (df_all_data['home_team']== team), 'local_acc_points'] = total_counter_points
                    if result_aux == 1:
                        counter_points_local = counter_points_local + 3
                        total_counter_points = total_counter_points + 3

                    elif result_aux == 0:
                        counter_points_local = counter_points_local + 1
                        total_counter_points = total_counter_points + 1

                    
                    if entrada_local == True: #evitem error partit 0
                        counter_partits_local = counter_partits_local + 1
                    entrada_local = True
                    
                    
                elif eslocal == 0:
                    # print(counter_partits_visitor)
                    #desem els punts a PviS abans d'actualitzar el counter:
                    df_all_data.loc[(df_all_data['season_id'] == season) & (df_all_data['round'] == round) & 
                                        (df_all_data['away_team'] == team), 'away_acc_pointsA'] = counter_points_visitor/(3*counter_partits_visitor)
                    df_all_data.loc[(df_all_data['season_id'] == season) & (df_all_data['round'] == round) &
                                            (df_all_data['away_team'] == team), 'away_acc_pointsL'] = counter_points_local/(3*counter_partits_local) #no incrementem el counter
                    
                    df_all_data.loc[(df_all_data['season_id'] == season) & (df_all_data['round'] == round) &
                                (df_all_data['away_team']== team), 'away_acc_points'] = total_counter_points
                    
                 
                    if result_aux == 0:
                        counter_points_visitor = counter_points_visitor + 1
                        total_counter_points = total_counter_points + 1

                    elif result_aux == -1: #el local ha perdut --> visitant ha guanyat
                        counter_points_visitor = counter_points_visitor + 3
                        total_counter_points = total_counter_points + 3

                    if entrada_visitor == True: #evitem error partit 0
                        counter_partits_visitor = counter_partits_visitor + 1
                    entrada_visitor = True
                    
                    
            else:
                raise(ValueError)
                
                
                          
                


100%|██████████| 72/72 [15:24<00:00, 12.84s/it]


In [34]:
df_all_data[(df_all_data["round"]==2) & (df_all_data["League"]== "La Liga") & (df_all_data["season_id"]==21694)][["home_team","away_team","local_acc_pointsL","local_acc_pointsA","away_acc_pointsL","away_acc_pointsA","local_acc_points","away_acc_points"]]

home_team        away_team  local_acc_pointsL  \
24096          Mallorca       Villarreal           0.000000   
24108          Valencia       Las Palmas           0.000000   
24132     Real Sociedad    Celta de Vigo           0.333333   
24144           Almería      Real Madrid           0.000000   
24159           Osasuna    Athletic Club           0.000000   
24188            Girona           Getafe           0.000000   
24192      FC Barcelona            Cádiz           0.000000   
24203        Real Betis  Atlético Madrid           0.000000   
24207  Deportivo Alavés          Sevilla           0.000000   
24215           Granada   Rayo Vallecano           0.000000   

       local_acc_pointsA  away_acc_pointsL  away_acc_pointsA  \
24096           0.333333          0.000000               0.0   
24108           1.000000          0.333333               0.0   
24132           0.000000          0.000000               0.0   
24144           0.000000          0.000000               1.0   
24159           1.000000          0.000000               0.0   
24188           0.333333          0.333333               0.0   
24192           0.333333          1.000000               0.0   
24203           1.000000          1.000000               0.0   
24207           0.000000          0.000000               0.0   
24215           0.000000          0.000000               1.0   

       local_acc_points  away_acc_points  
24096               1.0              0.0  
24108               3.0              1.0  
24132               1.0              0.0  
24144               0.0              3.0  
24159               3.0              0.0  
24188               1.0              1.0  
24192               1.0              3.0  
24203               3.0              3.0  
24207               0.0              0.0  
24215               0.0              3.0

In [35]:
df_all_data[(df_all_data["round"]==38) & (df_all_data["League"]== "La Liga") & (df_all_data["season_id"]==21694)][["home_team","away_team","local_acc_points","away_acc_points"]]

home_team         away_team  local_acc_points  away_acc_points
28650          Girona           Granada              78.0             21.0
28651         Osasuna        Villarreal              44.0             52.0
28653   Real Sociedad   Atlético Madrid              60.0             73.0
28665  Rayo Vallecano     Athletic Club              38.0             65.0
28666         Almería             Cádiz              18.0             33.0
28672     Real Madrid        Real Betis              94.0             56.0
28673          Getafe          Mallorca              43.0             37.0
28675   Celta de Vigo          Valencia              40.0             48.0
28676      Las Palmas  Deportivo Alavés              39.0             45.0
28705         Sevilla      FC Barcelona              41.0             82.0

## Creating month variable

In [36]:
#We create a new variable that is the month of the season in which the match is played. 1 will be August and 12 will be July.
#For this, we take the date of the match and subtract 7 months from it.

df_all_data['month'] = df_all_data['date'].str[5:7]
df_all_data['month'] = df_all_data['month'].astype(int)
if df_all_data['month'].max() > 12:
    raise Exception('Error: maximum month is 12')
if df_all_data['month'].min() < 1:
    raise Exception('Error: minimum month is 1') 


df_all_data['month'] = df_all_data['month'] - 7
df_all_data.loc[df_all_data['month'] < 1, 'month'] = df_all_data['month'] + 12

# Attempt to convert the 'date' column to datetime, handling errors by setting them to NaT.
df_all_data['date'] = pd.to_datetime(df_all_data['date'], errors='coerce')

# Now, you can use the .dt accessor
df_all_data['day_of_week'] = df_all_data['date'].dt.dayofweek + 1

Thus, the biggest months will be the final ones, when there is more to be decided, and the minimum will correspond to the earliest rounds

In [37]:
df_all_data[df_all_data["League"]=="Bundesliga"]["home_team"].unique()

array(['FC Bayern München', 'Hertha BSC', 'Werder Bremen', 'SC Freiburg',
       'VfL Wolfsburg', 'Fortuna Düsseldorf', 'Borussia Mönchengladbach',
       'FSV Mainz 05', 'Borussia Dortmund', 'Hannover 96',
       'Eintracht Frankfurt', 'FC Augsburg', 'TSG Hoffenheim',
       'Bayer 04 Leverkusen', 'Nürnberg', 'VfB Stuttgart', 'RB Leipzig',
       'Schalke 04', 'FC Union Berlin', 'FC Köln', 'Paderborn',
       'DSC Arminia Bielefeld', 'VfL Bochum 1848', 'SpVgg Greuther Fürth',
       'Heidenheim', 'Darmstadt 98', 'St. Pauli', 'Holstein Kiel'],
      dtype=object)

In [38]:
df_all_data["League"].unique()

array(['Eredivisie', 'Ligue 1', 'Turkish Süper Lig', 'Premier League',
       'Primeira Liga', 'La Liga', 'Serie A', 'Bundesliga',
       'Championship (2nd UK)', 'La Liga 2', 'Ekstraklasa (Poland)',
       'Serie B'], dtype=object)

## Creating a variable for active champions league teams 

In [39]:
champions_league_data = {
    "season_18_19" : {
    "phases": {
        "group_stage": {
            "start_date": "2018-09-18",
            "final_date": "2018-12-12",
            "teams": ["Real Madrid", "Roma", "Manchester United", "Juventus", "Valencia", "FC Bayern München", "Ajax", "Benfica", "Manchester City", "Olympique Lyonnais", "TSG Hoffenheim", "Barcelona", "Tottenham Hotspur", "Inter", "PSV", "Liverpool", "Paris Saint Germain", "Napoli", "Borussia Dortmund", "Atlético Madrid", "Club Brugge", "Monaco", "Porto", "Schalke 04", "Galatasaray"]
        },
        "round_of_16": {
            "start_date": "2019-02-12",
            "final_date": "2019-03-13",
            "teams": ["Borussia Dortmund", "Tottenham Hotspur", "Real Madrid", "Ajax", "Paris Saint Germain", "Manchester United", "Porto", "Roma", "FC Bayern München", "Liverpool", "Barcelona", "Olympique Lyonnais", "Manchester City", "Schalke 04", "Juventus", "Atlético Madrid"]
        },
        "quarter_finals": {
            "start_date": "2019-04-09",
            "final_date": "2019-04-17",
            "teams": ["Ajax", "Juventus", "Liverpool", "Porto", "Tottenham Hotspur", "Manchester City", "Barcelona", "Manchester United"]
        },
        "semi_finals": {
            "start_date": "2019-04-30",
            "final_date": "2019-05-08",
            "teams": ["Tottenham Hotspur", "Ajax", "Barcelona", "Liverpool"]
        },
        "final": {
            "start_date": "2019-06-01",
            "final_date": "2019-06-01",
            "teams": ["Tottenham Hotspur", "Liverpool"]
        }
    } 
    },


"season_19_20" : {
    "phases": {
        "group_stage": {
            "start_date": "2019-09-17",
            "final_date": "2019-12-11",
            "teams": ["Paris Saint Germain", "Real Madrid", "Club Brugge", "Galatasaray", "FC Bayern München", "Tottenham Hotspur", "Manchester City", "Atalanta", "Juventus", "Atlético Madrid", "Bayer 04 Leverkusen", "Liverpool", "Napoli", "Genk", "Barcelona", "Borussia Dortmund", "Inter", "RB Leipzig", "Benfica", "Olympique Lyonnais", "Chelsea", "Ajax", "Valencia", "LOSC Lille"]
        },
        "round_of_16": {
            "start_date": "2020-02-18",
            "final_date": "2020-08-07",
            "teams": ["Borussia Dortmund", "Paris Saint Germain", "Real Madrid", "Manchester City", "Atalanta", "Valencia", "RB Leipzig", "Tottenham Hotspur", "Olympique Lyonnais", "Juventus", "Napoli", "Barcelona", "Chelsea", "FC Bayern München", "Liverpool", "Atlético Madrid"]
        },
        "quarter_finals": {
            "start_date": "2020-08-12",
            "final_date": "2020-08-15",
            "teams": ["Atalanta", "Paris Saint Germain", "RB Leipzig", "Atlético Madrid", "FC Barcelona", "FC Bayern München", "Manchester City", "Olympique Lyonnais"]
        },
        "semi_finals": {
            "start_date": "2020-08-18",
            "final_date": "2020-08-19",
            "teams": ["RB Leipzig", "Paris Saint Germain", "FC Bayern München", "Olympique Lyonnais"]
        },
        "final": {
            "start_date": "2020-08-23",
            "final_date": "2020-08-23",
            "teams": ["Paris Saint Germain", "FC Bayern München"]
        }
    } 
    },

    "season_20_21" : {
    "phases": {
        "group_stage": {
            "start_date": "2020-10-20",
            "final_date": "2020-12-09",
            "teams": ["FC Bayern München", "Atlético Madrid", "Real Madrid", "Inter", "Borussia Mönchengladbach", "Manchester City", "FC Porto", "Olympique Marseille", "Liverpool", "Ajax", "Atalanta", "Chelsea", "Sevilla", "Rennes", "Borussia Dortmund", "Lazio", "Club Brugge", "Juventus", "FC Barcelona", "Paris Saint Germain", "RB Leipzig", "İstanbul Başakşehir", "Manchester United"]
        },
        "round_of_16": {
            "start_date": "2021-02-16",
            "final_date": "2021-03-17",
            "teams": ["Borussia Mönchengladbach", "Real Madrid", "FC Porto", "Manchester City", "Atalanta", "Liverpool", "Sevilla", "Borussia Dortmund", "FC Barcelona", "Paris Saint Germain", "RB Leipzig", "FC Bayern München", "Atlético Madrid", "Chelsea", "Lazio", "Juventus"]
        },
        "quarter_finals": {
            "start_date": "2021-04-06",
            "final_date": "2021-04-14",
            "teams": ["Real Madrid", "Liverpool", "FC Porto", "Chelsea", "Borussia Dortmund", "Manchester City", "Paris Saint Germain", "FC Bayern München"]
        },
        "semi_finals": {
            "start_date": "2021-04-27",
            "final_date": "2021-05-05",
            "teams": ["Real Madrid", "Chelsea", "Manchester City", "Paris Saint Germain"]
        },
        "final": {
            "start_date": "2021-05-29",
            "final_date": "2021-05-29",
            "teams": ["Manchester City", "Chelsea"]
        }
    }
},




    "season_21_22": {
        "phases": {
            "group_stage": {
                "start_date": "2021-09-14", "final_date": "2021-12-08",
                "teams": ["Manchester City", "Paris Saint Germain", "RB Leipzig", "Liverpool", "Atlético Madrid", "Porto", "Milan", "Inter", "Real Madrid", "Barcelona", "Benfica", "Manchester United", "Villarreal", "LOSC Lille", "Sevilla", "Juventus", "Chelsea", "Sporting CP","Ajax","FC Bayern München","Club Brugge","Beşiktaş","Atalanta","VfL Wolfsburg"]
            },
            "round_of_16": {
                "start_date": "2022-02-15", "final_date": "2022-03-16",
                "teams": ["Manchester City", "Paris Saint Germain", "Liverpool","Ajax", "Atlético Madrid", "Inter", "Real Madrid", "Benfica", "Villarreal", "Manchester United", "LOSC Lille", "Chelsea", "Juventus", "Sporting CP","FC Bayern München"]
            },
            "quarter_finals": {
                "start_date": "2022-04-05", "final_date": "2022-04-13",
                "teams": ["Manchester City", "Atlético Madrid", "Liverpool", "Benfica", "Real Madrid", "Chelsea", "Villarreal", "FC Bayern München"]
            },
            "semi_finals": {
                "start_date": "2022-04-26", "final_date": "2022-05-04",
                "teams": ["Manchester City", "Real Madrid", "Liverpool", "Villarreal"]
            },
            "final": {
                "start_date": "2022-05-28", "final_date": "2022-05-28",
                "teams": ["Real Madrid", "Liverpool"]
            }
        }
    },
    "season_22_23": {
        "phases": {
            "group_stage": {
                "start_date": "2022-09-06", "final_date": "2022-11-02",
                "teams": ["Real Madrid", "RB Leipzig", "Manchester City", "Borussia Dortmund", "Sevilla", "Paris Saint Germain", "Juventus", "Benfica", "Milan", "Chelsea", "FC Bayern München", "Barcelona", "Inter", "Napoli", "Liverpool", "Ajax", "Porto", "Atlético Madrid", "Bayer 04 Leverkusen", "Tottenham Hotspur", "Eintracht Frankfurt", "Sporting CP","Club Brugge","Olympique Marseille"]
            },
            "round_of_16": {
                "start_date": "2023-02-14", "final_date": "2023-03-15",
                "teams": ["Real Madrid", "Liverpool", "Manchester City", "RB Leipzig", "Benfica", "Chelsea", "Borussia Dortmund", "Tottenham Hotspur", "Milan", "FC Bayern München", "Paris Saint Germain", "Napoli", "Eintracht Frankfurt", "Inter", "Porto","Club Brugge"]
            },
            "quarter_finals": {
                "start_date": "2023-04-11", "final_date": "2023-04-19",
                "teams": ["Real Madrid", "Chelsea", "Manchester City", "FC Bayern München", "Benfica", "Inter", "Milan", "Napoli"]
            },
            "semi_finals": {
                "start_date": "2023-05-09", "final_date": "2023-05-17",
                "teams": ["Real Madrid", "Manchester City", "Inter", "Milan"]
            },
            "final": {
                "start_date": "2023-06-10", "final_date": "2023-06-10",
                "teams": ["Manchester City", "Inter"]
            }
        }
    },
    "season_23_24": {
        "phases": {
            "group_stage": {
                "start_date": "2023-09-19", "final_date": "2023-12-13",
                "teams": ["Manchester City", "RB Leipzig", "Atlético Madrid", "Lazio", "Feyenoord", "Barcelona", "Porto", "Napoli", "Real Madrid", "FC Bayern München", "Manchester United", "Sevilla", "Arsenal", "PSV", "Inter", "Benfica", "Milan", "Paris Saint Germain", "Borussia Dortmund","Real Sociedad","Antwerp","Club Brugge","Lens","Sporting Braga","FC Union Berlin", "Newcastle United"]
            },
            "round_of_16": {
                "start_date": "2024-02-13", "final_date": "2024-03-13",
                "teams": ["FC Bayern München", "Arsenal", "Porto", "Real Madrid", "RB Leipzig", "Manchester City", "Barcelona", "Napoli", "Real Sociedad", "Paris Saint Germain", "Atlético Madrid", "Inter", "Borussia Dortmund", "PSV", "Lazio"]
            },
            "quarter_finals": {
                "start_date": "2024-04-09", "final_date": "2024-04-17",
                "teams": ["Arsenal", "FC Bayern München", "Real Madrid", "Manchester City", "Barcelona", "Paris Saint Germain", "Atlético Madrid", "Borussia Dortmund"]
            },
            "semi_finals": {
                "start_date": "2024-04-30", "final_date": "2024-05-08",
                "teams": ["FC Bayern München", "Real Madrid", "Paris Saint Germain", "Borussia Dortmund"]
            },
            "final": {
                "start_date": "2024-06-01", "final_date": "2024-06-01",
                "teams": ["Real Madrid", "Borussia Dortmund"]
            }
        }
    },
"season_24_25" : {
    "phases": {
        "league_phase": {
            "start_date": "2024-09-17",
            "final_date": "2025-01-29",
            "teams": ["Real Madrid", "Atalanta", "Manchester City", "Arsenal", "Liverpool", "Aston Villa", "Barcelona", "Girona", "Atlético Madrid", "Bayer 04 Leverkusen", "VfB Stuttgart", "FC Bayern München", "RB Leipzig", "Borussia Dortmund", "Inter", "Milan", "Juventus", "Bologna", "Paris Saint-Germain", "Monaco", "Brest", "PSV", "Feyenoord", "Sporting CP", "Benfica", "Club Brugge", "Galatasaray", "Lille", "Twente", "Union Saint-Gilloise"]
        },
        "knockout_phase_play_offs": {
            "start_date": "2025-02-11",
            "final_date": "2025-02-19",
            "teams": ["Atalanta", "Borussia Dortmund", "Real Madrid", "FC Bayern München", "Milan", "PSV", "Paris Saint-Germain", "Benfica", "Monaco", "Brest", "Feyenoord", "Juventus", "Manchester City", "Sporting CP", "Club Brugge"]
        },
        "round_of_16": {
            "start_date": "2025-03-04",
            "final_date": "2025-03-12",
            "teams": ["Liverpool", "Barcelona", "Arsenal", "Inter", "Atlético Madrid", "Bayer 04 Leverkusen", "Lille", "Aston Villa", "Benfica", "Paris Saint-Germain", "FC Bayern München", "RB Leipzig", "Real Madrid", "Borussia Dortmund", "Feyenoord", "Club Brugge"]
        },
        "quarter_finals": {
            "start_date": "2025-04-08",
            "final_date": "2025-04-16",
            "teams": ["Aston Villa", "Borussia Dortmund", "FC Bayern München", "Real Madrid", "FC Barcelona", "Paris Saint-Germain", "Inter", "Arsenal"]
        },
        "semi_finals": {
            "start_date": "2025-04-29",
            "final_date": "2025-05-07",
            "teams": ["Arsenal", "FC Barcelona", "Paris Saint-Germain", "Inter"]
        },
        "final": {
            "start_date": "2025-05-31",
            "final_date": "2025-05-31",
            "teams": ["Inter", "Paris Saint-Germain"]
        }
    }
}
}

In [40]:
import pandas as pd
from datetime import datetime

def check_champions_league_participation(row):
    """
    For each row in df, checks if the match date falls within a CL phase period and if the teams participated.
    Adds two new columns: 'local_plays_CL' and 'away_plays_CL'.
    """
    
    def is_team_in_cl(date, team):
        for season, data in champions_league_data.items():
            for phase, phase_data in data["phases"].items():
                start_date = datetime.strptime(phase_data["start_date"], "%Y-%m-%d")
                final_date = datetime.strptime(phase_data["final_date"], "%Y-%m-%d")
                
                if start_date <= date <= final_date and team in phase_data["teams"]:
                    return 1
        return 0
    
    row['date'] = pd.to_datetime(row['date'])
    row['local_plays_CL'] = is_team_in_cl(row['date'], row['home_team'])
    row['away_plays_CL'] = is_team_in_cl(row['date'], row['away_team'])
    
    return row
df_all_data = df_all_data.apply(check_champions_league_participation, axis=1)


In [41]:
df_all_data[df_all_data["local_acc_points"].isna()][["season_id","League","season"]].value_counts()

Series([], Name: count, dtype: int64)

In [42]:
df_all_data

League  away_acc_corners  away_acc_goals  \
55               Eredivisie          0.000000        0.000000   
58                  Ligue 1          0.000000        0.000000   
59        Turkish Süper Lig          0.000000        0.000000   
60           Premier League          0.000000        0.000000   
61            Primeira Liga          0.000000        0.000000   
...                     ...               ...             ...   
33361  Ekstraklasa (Poland)          3.932389        1.096773   
33362             La Liga 2          4.525978        1.342330   
33364        Premier League          6.714834        2.315297   
33365        Premier League          3.541656        1.458298   
33366        Premier League          6.031074        1.571093   

       away_acc_possession  away_acc_red_cards  away_acc_yellow_cards  \
55                0.000000            0.000000               0.000000   
58                0.000000            0.000000               0.000000   
59                0.000000            0.000000               0.000000   
60                0.000000            0.000000               0.000000   
61                0.000000            0.000000               0.000000   
...                    ...                 ...                    ...   
33361            39.393032            0.129137               2.550993   
33362            45.438517            0.131673               2.264002   
33364            58.194348            0.057191               1.828427   
33365            47.237548            0.057191               2.116041   
33366            47.827014            0.057167               2.571860   

                                              away_bench  away_corners  \
55     [{150982: {'team_id': 1053, 'position_id': 25,...      1.000000   
58     [{96587: {'team_id': 289, 'position_id': 24, '...      1.000000   
59     [{201416: {'team_id': 34, 'position_id': 25, '...      4.000000   
60     [{612: {'team_id': 42, 'position_id': 25, 'for...      5.000000   
61     [{161798: {'team_id': 830, 'position_id': 27, ...      2.000000   
...                                                  ...           ...   
33361                                                 []      3.875000   
33362                                                 []      4.263158   
33364                                                 []      7.000000   
33365                                                 []      3.611111   
33366                                                 []      6.000000   

      away_formation  away_goals  ... local_acc_pointsL  local_acc_pointsA  \
55             4-3-3         3.0  ...          0.000000           0.000000   
58           4-2-3-1         0.0  ...          0.000000           0.000000   
59           4-2-3-1         3.0  ...          0.000000           0.000000   
60           4-2-3-1         1.0  ...          0.000000           0.000000   
61           4-2-3-1         2.0  ...          0.000000           0.000000   
...              ...         ...  ...               ...                ...   
33361           None         0.0  ...          0.500000           0.291667   
33362           None         0.0  ...          0.543860           0.383333   
33364           None         0.0  ...          0.537037           0.481481   
33365           None         0.0  ...          0.407407           0.500000   
33366           None         0.0  ...          0.722222           0.481481   

       away_acc_pointsL away_acc_pointsA  local_acc_points away_acc_points  \
55             0.000000         0.000000               0.0             0.0   
58             0.000000         0.000000               0.0             0.0   
59             0.000000         0.000000               0.0             0.0   
60             0.000000         0.000000               0.0             0.0   
61             0.000000         0.000000               0.0             0.0   
...                 ...              ...               ...           

In [43]:
#We will do a ranking of the season. We will order total_punts from highest to lowest and assign a number being 1 the highest. 
# In case of a tie we will assign more than one number to the same value.


for season in (season_list):
    for round_aux in range(1,int(df_all_data.loc[df_all_data["season_id"] == season, "round"].unique().max())+1):
        round  = float(round_aux)

        ll_total_punts_loc = df_all_data.loc[(df_all_data['season_id'] == season) & (df_all_data['round'] == round), 'local_acc_points'].tolist()
        ll_total_punts_vis = df_all_data.loc[(df_all_data['season_id'] == season) & (df_all_data['round'] == round), 'away_acc_points'].tolist()

        ll_total_punts = ll_total_punts_loc + ll_total_punts_vis

        set_total_punts = set(ll_total_punts)
        ll_total_punts = list(set_total_punts)
        #convert to float 
        ll_total_punts = [float(i) for i in ll_total_punts]
        ll_total_punts.sort(reverse=True)
        #print(ll_total_punts)  
          

        #We assign the position +1 to each team that has that score.
        df_all_data.loc[(df_all_data['season_id'] == season) & (df_all_data['round'] == round), 'local_rk'] = -1
        df_all_data.loc[(df_all_data['season_id'] == season) & (df_all_data['round'] == round), 'away_rk'] = -1
        
        def get_rank(x):
            try:
                return list(ll_total_punts).index(x) + 1
            except ValueError:
                raise ValueError(f"{x} not in list for season {season}, round {round}, total_punts {ll_total_punts}")

        
        df_all_data.loc[(df_all_data['season_id'] == season) & (df_all_data['round'] == round), 'local_rk'] = df_all_data.loc[(df_all_data['season_id'] == season) & (df_all_data['round'] == round), 'local_acc_points'].apply(get_rank)
        df_all_data.loc[(df_all_data['season_id'] == season) & (df_all_data['round'] == round), 'away_rk'] = df_all_data.loc[(df_all_data['season_id'] == season) & (df_all_data['round'] == round), 'away_acc_points'].apply(get_rank)
        



## Drop Atypical Matches II

In [44]:
#We delete those matches where state_id !=5 , which mean that did not end at Full Time. (Some of them might be postponed)
df_all_data = df_all_data[df_all_data["state_id"] == 5]  #We delete it here so the cumulative metrics can be computed.


## Remove rows with no formations info

In [45]:
df_all_data = df_all_data[df_all_data["formations"] != "[]"]

## Drop old columns

In [46]:
df_all_data.drop('bench', axis=1, inplace=True)
df_all_data.drop('lineup', axis=1, inplace=True)
df_all_data.drop('formations', axis=1, inplace=True)
df_all_data.drop('lineups', axis=1, inplace=True)
df_all_data.drop('round_id', axis=1, inplace=True)
# df_all_data.drop('season_id', axis=1, inplace=True)
df_all_data.drop('state_id', axis=1, inplace=True)
df_all_data.drop('weather', axis=1, inplace=True)

In [47]:
# df_all_data[df_all_data["League"]=="La Liga"][["home_team","away_team","local_rk","away_rk","local_acc_points","away_acc_points"]].tail(10)

In [48]:
df_all_data.shape

(26488, 56)

- mirar d'agrupar les formacions possibles
- mirar d'ordenar-les de defensiva i ofensiva. (mirant taxa de gols??)   Parlar amb el Juan
- target variable: diferència de gols. Provar tmb 'winner'. Regressió vs classificació

In [49]:
formations_data = pd.concat([df_all_data["away_formation"],df_all_data["local_formation"]])
print(formations_data.value_counts()/len(formations_data)*100)
print(len(formations_data.unique()) )

4-2-3-1      29.700242
4-3-3        15.646708
4-4-2        13.028541
3-4-2-1       7.605331
3-5-2         7.441105
4-1-4-1       5.440199
3-4-3         4.637949
3-4-1-2       3.745092
4-3-1-2       2.650257
5-3-2         2.465267
5-4-1         1.812141
4-4-1-1       1.581848
3-1-4-2       1.030655
4-3-2-1       0.811688
4-5-1         0.607822
3-5-1-1       0.579508
4-2-2-2       0.509665
4-1-3-2       0.443597
3-2-4-1       0.077394
4-1-2-1-2     0.043416
3-3-3-1       0.037753
3-3-2-2       0.028315
4-2-1-3       0.022652
3-3-1-3       0.022652
4-1-2-3       0.015101
5-2-3         0.005663
3-2-3-2       0.003775
4-2-1-2-1     0.001888
4-2-4         0.001888
5-3-1-1       0.001888
Name: count, dtype: float64
30


In [50]:
# "4-1-2-3", "4-2-1-3" --> "4-3-3"
# "4-1-2-1-2", "4-2-2-2"  --> "4-4-2"
# "5-3-1-1" --> "5-4-1"
# "3-2-3-2" , "3-3-2-2", "3-1-4-2" --> "3-5-2"
# "3-3-1-3"  --> "3-4-3"
# "3-3-3-1"  --> "3-6-1"   ???  "3-3-4"   (al ser un 0.5% potser millor passar-ho a una "4-5-1"??)
# "3-2-4-1"  -->"3-6-1" ??  "5-4-1"
# "3-5-1-1"  --> "3-6-1" ?? "4-5-1"    !!!ni idea
# "4-3-2-1"  --> "4-5-2" ?? "4-3-3"
# "4-1-3-2" --> "5-3-2" ?? "4-4-2"
# "4-4-1-1" --> "4-5-1"   !!tot i diferència en possesió?


In [51]:
popular_formations = ["4-2-3-1", "4-3-3", "4-4-2", "3-4-2-1", "3-5-2", "3-4-3", "5-3-2","3-4-1-2","4-1-4-1","4-3-1-2","5-4-1","4-4-1-1","4-5-1"]


average_possession = df_all_data.groupby("local_formation")["local_possession"].mean()
average_possession_df = average_possession.to_frame(name="average_possession")

filtered_possession = average_possession_df[average_possession_df.index.isin(popular_formations)].sort_values(by="average_possession", ascending=False)
filtered_possession.head(13)

average_possession
local_formation                    
4-3-3                     53.527527
4-2-3-1                   52.224720
3-4-2-1                   51.411201
4-1-4-1                   50.917073
4-3-1-2                   50.849582
3-4-1-2                   50.546922
3-4-3                     50.390690
4-4-2                     49.435430
4-4-1-1                   48.970149
3-5-2                     48.603439
4-5-1                     48.112782
5-3-2                     45.568966
5-4-1                     42.344262

In [52]:
average_possession = df_all_data.groupby("away_formation")["away_possession"].mean()
average_possession_df = average_possession.to_frame(name="average_possession")

filtered_possession = average_possession_df[average_possession_df.index.isin(popular_formations)].sort_values(by="average_possession", ascending=False)
filtered_possession.head(13)

average_possession
away_formation                    
4-3-3                    52.020859
4-2-3-1                  49.963154
3-4-2-1                  49.193942
4-3-1-2                  49.167638
4-1-4-1                  48.639254
3-4-1-2                  48.310171
3-4-3                    48.055821
4-4-2                    47.153312
3-5-2                    46.994068
4-4-1-1                  46.591743
4-5-1                    44.000000
5-3-2                    42.495868
5-4-1                    40.321549

## Formation groupping
Formations will be grouped into 5 different ones to ease and enhance the analysis 

In [ ]:
#We will compute a function which groups the football formations into 5-8 groups (to be defined later)
# "4-1-2-3", "4-2-1-3" --> "4-3-3"
# "4-1-2-1-2", "4-2-2-2"  --> "4-4-2"
# "5-3-1-1" --> "5-4-1"
# "3-2-3-2" , "3-3-2-2", "3-1-4-2" --> "3-5-2"
# "3-3-1-3"  --> "3-4-3"
# "3-3-3-1"  --> "3-6-1"   ???  "3-3-4"   (al ser un 0.5% potser millor passar-ho a una "4-5-1"??)
# "3-2-4-1"  -->"3-6-1" ??  "5-4-1"
# "3-5-1-1"  --> "3-6-1" ?? "4-5-1"    
# "4-3-2-1"  --> "4-5-1" ?? "4-3-3"
# "4-1-3-2" --> "5-3-2" ?? "4-4-2"
# "4-4-1-1" --> "4-5-1"   !!tot i diferència en possesió?
# def map_formations(row_column):
#     if(row_column=="4-1-2-3" or row_column=="4-2-1-3"):
#         return "4-3-3"
#     elif(row_column=="4-1-2-1-2" or row_column=="4-2-2-2"):
#         return "4-4-2"
#     elif(row_column=="5-3-1-1"):
#         return "5-4-1"
#     elif(row_column=="3-2-3-2" or row_column=="3-3-2-2" or row_column=="3-1-4-2" or row_column=="3-4-1-2"):
#         return "3-5-2"
#     elif(row_column=="3-3-1-3"):
#         return "3-4-3"
#     elif(row_column=="3-3-3-1"):
#         return "5-4-1" 
#     elif(row_column=="3-2-4-1"):
#         return "5-4-1"
#     elif(row_column=="3-5-1-1"):
#         return "3-5-2"
#     elif(row_column=="4-3-2-1"):
#         return "4-3-3"
#     elif(row_column=="4-1-3-2"):
#         return "4-4-2"
#     elif(row_column=="4-4-1-1"): 
#         return "4-4-2"
#     elif(row_column=="4-5-1"): 
#         return "4-3-3"
#     elif(row_column=="4-3-1-2"):
#         return "4-3-3"
#     elif(row_column=="3-4-2-1"):
#         return "3-4-3"
#     elif(row_column=="4-1-4-1"): 
#         return "5-4-1"
#     elif(row_column=="5-3-2"):
#         return "3-5-2"
#     elif(row_column=='5-2-3'):
#         return "5-4-1"
#     elif(row_column=="4-2-4"):
#         return "4-4-2"
#     elif(row_column=="4-2-1-2-1"):
#         return "4-2-3-1"
#     else:
#         return row_column
    
def map_formations(row_column):
    # 4-3-3 group
    if row_column in ["4-1-2-3", "4-2-1-3", "4-3-2-1", "4-5-1", "4-3-1-2"]:
        return "4-3-3"
    # 4-4-2 group
    elif row_column in ["4-1-2-1-2", "4-2-2-2", "4-1-3-2", "4-4-1-1", "4-2-4"]:
        return "4-4-2"
    # 5-4-1 group
    elif row_column in ["5-3-1-1", "3-3-3-1", "3-2-4-1", "4-1-4-1", "5-2-3"]:
        return "5-4-1"
    # 3-5-2 group
    elif row_column in ["3-2-3-2", "3-3-2-2", "3-1-4-2", "3-5-1-1", "5-3-2","3-4-1-2"]:
        return "3-5-2"
    # 3-4-3 group
    elif row_column in ["3-3-1-3", "3-4-2-1"]:
        return "3-4-3"
    elif(row_column=="4-2-1-2-1"):
        return "4-2-3-1"
    
    # leave as is for all other formations
    else:
        return row_column
    
df_all_data["local_formation"] = df_all_data["local_formation"].apply(map_formations)
df_all_data["away_formation"] = df_all_data["away_formation"].apply(map_formations)
    

In [54]:
df_all_data["local_formation"].value_counts()/len(df_all_data)*100

local_formation
4-2-3-1    30.391121
4-3-3      19.967532
4-4-2      15.969496
3-5-2      14.708547
3-4-3      12.058291
5-4-1       6.905014
Name: count, dtype: float64

In [55]:
df_all_data["away_formation"].value_counts()/len(df_all_data)*100

away_formation
4-2-3-1    29.013138
4-3-3      19.540924
3-5-2      15.878889
4-4-2      15.248414
3-4-3      12.473573
5-4-1       7.845062
Name: count, dtype: float64

## Change in the format 
We will analyse main_team vs rival_team and duplicate the dataset, including the variable side which states H/A. 

In [56]:
df_copia = df_all_data.copy()
# df_all_data = df_copia

In [57]:
df_all_data

League  away_acc_corners  away_acc_goals  \
55               Eredivisie          0.000000        0.000000   
58                  Ligue 1          0.000000        0.000000   
59        Turkish Süper Lig          0.000000        0.000000   
60           Premier League          0.000000        0.000000   
61            Primeira Liga          0.000000        0.000000   
...                     ...               ...             ...   
33223             La Liga 2          4.377261        0.540195   
33222               La Liga          4.273044        1.212264   
33224         Primeira Liga          5.542759        1.840623   
33225               Serie A          3.796535        1.558431   
33226  Ekstraklasa (Poland)          4.899928        1.065667   

       away_acc_possession  away_acc_red_cards  away_acc_yellow_cards  \
55                0.000000            0.000000               0.000000   
58                0.000000            0.000000               0.000000   
59                0.000000            0.000000               0.000000   
60                0.000000            0.000000               0.000000   
61                0.000000            0.000000               0.000000   
...                    ...                 ...                    ...   
33223            47.487531            0.108189               1.972222   
33222            45.867530            0.000000               2.453166   
33224            61.800137            0.064551               2.773986   
33225            49.732373            0.058876               2.058011   
33226            48.756429            0.200192               1.800884   

                                              away_bench  away_corners  \
55     [{150982: {'team_id': 1053, 'position_id': 25,...           1.0   
58     [{96587: {'team_id': 289, 'position_id': 24, '...           1.0   
59     [{201416: {'team_id': 34, 'position_id': 25, '...           4.0   
60     [{612: {'team_id': 42, 'position_id': 25, 'for...           5.0   
61     [{161798: {'team_id': 830, 'position_id': 27, ...           2.0   
...                                                  ...           ...   
33223  [{525018: {'team_id': 8396, 'position_id': 24,...           0.0   
33222  [{186878: {'team_id': 459, 'position_id': 25, ...           7.0   
33224  [{37421962: {'team_id': 652, 'position_id': 25...           4.0   
33225  [{129203: {'team_id': 109, 'position_id': 24, ...           5.0   
33226  [{25174: {'team_id': 7216, 'position_id': 27, ...           6.0   

      away_formation  away_goals  ... away_acc_pointsL  away_acc_pointsA  \
55             4-3-3         3.0  ...         0.000000          0.000000   
58           4-2-3-1         0.0  ...         0.000000          0.000000   
59           4-2-3-1         3.0  ...         0.000000          0.000000   
60           4-2-3-1         1.0  ...         0.000000          0.000000   
61           4-2-3-1         2.0  ...         0.000000          0.000000   
...              ...         ...  ...              ...               ...   
33223        4-2-3-1         0.0  ...         0.228070          0.228070   
33222        4-2-3-1         1.0  ...         0.588235          0.274510   
33224          3-4-3         2.0  ...         0.812500          0.541667   
33225          3-4-3         1.0  ...         0.685185          0.431373   
33226          3-4-3         3.0  ...         0.416667          0.133333   

       local_acc_points away_acc_points  month  day_of_week local_plays_CL  \
55                  0.0             0.0      1            5              0   
58                  0.0             0.0      1            5              0   
59                  0.0             0.0      1            5              0   
60                  0.0             0.0      1            5              0   
61                  0.0             0.0      1            5              0   
...                 ...             ...    ...          ...            ...   
33223          

In [58]:
df_all_data.columns

Index(['League', 'away_acc_corners', 'away_acc_goals', 'away_acc_possession',
       'away_acc_red_cards', 'away_acc_yellow_cards', 'away_bench',
       'away_corners', 'away_formation', 'away_goals', 'away_lineup',
       'away_possession', 'away_red_cards', 'away_team', 'away_yellow_cards',
       'clouds', 'date', 'events', 'feels_like', 'fixture_id', 'goals_diff',
       'home_team', 'humidity', 'local_acc_corners', 'local_acc_goals',
       'local_acc_possession', 'local_acc_red_cards', 'local_acc_yellow_cards',
       'local_bench', 'local_corners', 'local_formation', 'local_goals',
       'local_lineup', 'local_possession', 'local_red_cards',
       'local_yellow_cards', 'participants', 'round', 'season', 'season_id',
       'statistics', 'temperature', 'wind_speed', 'winner',
       'local_acc_pointsL', 'local_acc_pointsA', 'away_acc_pointsL',
       'away_acc_pointsA', 'local_acc_points', 'away_acc_points', 'month',
       'day_of_week', 'local_plays_CL', 'away_plays_CL', 'loc

In [59]:
#We will make an important change, as we want to study the impact al lineups before playing a game. Thus, the dataset instead of analyze a local team and a visitor team, we will have the main team and the rival team. So we will have to duplicate each row but changing home_team by away_team and viceversa, changing local_lineup by away_lineup and viceversa, and changing local_formation by away_formation and viceversa. Also, in winner column change 1 by -1 and -1 by 1. Also, change in column side, "H" per "A". Finally, we will rename the columns: main_team_id, main_team_players, main_team_lineup, rival_team_id, rival_team_players, rival_team_lineup, winner, side.
df_all_data["side"] = "H"
#First, we will duplicate the rows:
df_all_data2 = df_all_data.copy()
df_all_data2["side"] = "A"
df_all_data2["goals_diff"] *= -1 
df_all_data2["main_team"] = df_all_data2["away_team"]
df_all_data2["rival_team"] = df_all_data2["home_team"]
df_all_data2["winner"] = df_all_data2["winner"] * -1   # If it is 0 (draw), it will remain 0


df_all_data2["main_team_lineup"] = df_all_data2["away_lineup"]
df_all_data2["rival_team_lineup"] = df_all_data2["local_lineup"]
df_all_data2["main_team_bench"] = df_all_data2["away_bench"]
df_all_data2["rival_team_bench"] = df_all_data2["local_bench"]

df_all_data2["main_team_formation"] = df_all_data2["away_formation"]
df_all_data2["rival_team_formation"] = df_all_data2["local_formation"]

df_all_data2["main_team_acc_possession"] = df_all_data2["away_acc_possession"]
df_all_data2["rival_team_acc_possession"] = df_all_data2["local_acc_possession"]
df_all_data2["main_team_acc_goals"] = df_all_data2["away_acc_goals"]
df_all_data2["rival_team_acc_goals"] = df_all_data2["local_acc_goals"]
df_all_data2["main_team_acc_corners"] = df_all_data2["away_acc_corners"]
df_all_data2["rival_team_acc_corners"] = df_all_data2["local_acc_corners"]
df_all_data2["main_team_acc_yellow_cards"] = df_all_data2["away_acc_yellow_cards"]
df_all_data2["rival_team_acc_yellow_cards"] = df_all_data2["local_acc_yellow_cards"]
df_all_data2["main_team_acc_red_cards"] = df_all_data2["away_acc_red_cards"]
df_all_data2["rival_team_acc_red_cards"] = df_all_data2["local_acc_red_cards"]

df_all_data2["main_team_acc_pointsL"] = df_all_data2["away_acc_pointsL"]
df_all_data2["main_team_acc_pointsA"] = df_all_data2["away_acc_pointsA"]
df_all_data2["rival_team_acc_pointsL"] = df_all_data2["local_acc_pointsL"]
df_all_data2["rival_team_acc_pointsA"] = df_all_data2["local_acc_pointsA"]
df_all_data2["main_team_acc_points"] = df_all_data2["away_acc_points"]
df_all_data2["rival_team_acc_points"] = df_all_data2["local_acc_points"]


df_all_data2["main_team_plays_CL"] = df_all_data2["away_plays_CL"]
df_all_data2["rival_team_plays_CL"] = df_all_data2["local_plays_CL"]

df_all_data2["main_team_rk"] = df_all_data2["away_rk"]
df_all_data2["rival_team_rk"] = df_all_data2["local_rk"]


df_all_data2 = df_all_data2.drop(columns=["away_team", "home_team", "away_lineup", "local_lineup", "away_bench", "local_bench", "away_formation", "local_formation", 
                                          "away_possession", "local_possession", "away_goals", "local_goals", "away_corners", "local_corners", "away_yellow_cards", 
                                          "local_yellow_cards", "away_red_cards", "local_red_cards", 
                                          "away_acc_possession", "local_acc_possession", "away_acc_goals", "local_acc_goals", "away_acc_corners", "local_acc_corners", "away_acc_yellow_cards", 
                                          "local_acc_yellow_cards", "away_acc_red_cards", "local_acc_red_cards", 
                                          
                                          "away_acc_pointsL", "away_acc_pointsA", "local_acc_pointsL", "away_acc_points","local_acc_points",
                                          "local_acc_pointsA", "away_plays_CL", "local_plays_CL", "away_rk", "local_rk"])
print(df_all_data2.shape)
# df_all_data2.head()



(26488, 47)


In [60]:
ordered_columns = ['fixture_id','League','season', 'season_id', 'round','date',  'month', 'day_of_week', 'side', 'main_team','rival_team',
        'winner','goals_diff','main_team_formation', 'rival_team_formation', 'main_team_lineup', 'rival_team_lineup','main_team_bench', 'rival_team_bench',
        'main_team_acc_possession', 'rival_team_acc_possession', 'main_team_acc_goals', 'rival_team_acc_goals', 'main_team_acc_corners','rival_team_acc_corners',
        'main_team_acc_yellow_cards', 'rival_team_acc_yellow_cards', 'main_team_acc_red_cards','rival_team_acc_red_cards', 'main_team_acc_pointsL','main_team_acc_pointsA',
       'main_team_acc_points','rival_team_acc_pointsL','rival_team_acc_pointsA','rival_team_acc_points', 'main_team_plays_CL', 'rival_team_plays_CL',
       'main_team_rk', 'rival_team_rk','participants',  'statistics', 'events','clouds','feels_like','humidity','temperature', 'wind_speed']
df_all_data2 = df_all_data2[ordered_columns].sort_values(by='fixture_id')

In [61]:
df_all_data = df_all_data.rename(columns={"home_team": "main_team", "away_team": "rival_team", "local_lineup": "main_team_lineup", "away_lineup": "rival_team_lineup", 
                                          "local_formation": "main_team_formation", "away_formation": "rival_team_formation","local_bench": "main_team_bench", "away_bench": "rival_team_bench",
                                          "local_acc_possession": "main_team_acc_possession", "away_acc_possession": "rival_team_acc_possession","local_acc_corners": "main_team_acc_corners", "away_acc_corners": "rival_team_acc_corners",
                                          "local_acc_goals": "main_team_acc_goals", "away_acc_goals": "rival_team_acc_goals","local_acc_yellow_cards": "main_team_acc_yellow_cards", "away_acc_yellow_cards": "rival_team_acc_yellow_cards",
                                          "local_acc_red_cards": "main_team_acc_red_cards", "away_acc_red_cards": "rival_team_acc_red_cards","local_acc_pointsL": "main_team_acc_pointsL", "local_acc_pointsA": "main_team_acc_pointsA",
                                          "away_acc_pointsL": "rival_team_acc_pointsL", "away_acc_pointsA": "rival_team_acc_pointsA","local_acc_points": "main_team_acc_points", "away_acc_points": "rival_team_acc_points",
                                          "local_plays_CL": "main_team_plays_CL", "away_plays_CL": "rival_team_plays_CL","local_rk": "main_team_rk", "away_rk": "rival_team_rk"})

df_all_data = df_all_data[ordered_columns]

df_processed = pd.concat([df_all_data, df_all_data2], ignore_index=True)
df_processed = df_processed.sort_values("fixture_id")
df_processed.head(10)

fixture_id   League season  season_id  round                date  \
26488    10330189  Ligue 1  18-19      12935    1.0 2018-08-11 18:00:00   
17       10330189  Ligue 1  18-19      12935    1.0 2018-08-11 18:00:00   
36       10330190  Ligue 1  18-19      12935    1.0 2018-08-12 15:00:00   
26489    10330190  Ligue 1  18-19      12935    1.0 2018-08-12 15:00:00   
26490    10330191  Ligue 1  18-19      12935    1.0 2018-08-11 18:00:00   
18       10330191  Ligue 1  18-19      12935    1.0 2018-08-11 18:00:00   
32       10330192  Ligue 1  18-19      12935    1.0 2018-08-12 13:00:00   
26491    10330192  Ligue 1  18-19      12935    1.0 2018-08-12 13:00:00   
26492    10330193  Ligue 1  18-19      12935    1.0 2018-08-10 18:45:00   
1        10330193  Ligue 1  18-19      12935    1.0 2018-08-10 18:45:00   

       month  day_of_week side            main_team  ... main_team_rk  \
26488      1            6    A                Nîmes  ...          1.0   
17         1            6    H           Angers SCO  ...          1.0   
36         1            7    H             Bordeaux  ...          1.0   
26489      1            7    A           Strasbourg  ...          1.0   
26490      1            6    A               Rennes  ...          1.0   
18         1            6    H           LOSC Lille  ...          1.0   
32         1            7    H   Olympique Lyonnais  ...          1.0   
26491      1            7    A            Amiens SC  ...          1.0   
26492      1            5    A             Toulouse  ...          1.0   
1          1            5    H  Olympique Marseille  ...          1.0   

       rival_team_rk                                       participants  \
26488            1.0  [{'id': 776, 'sport_id': 1, 'country_id': 17, ...   
17               1.0  [{'id': 776, 'sport_id': 1, 'country_id': 17, ...   
36               1.0  [{'id': 3562, 'sport_id': 1, 'country_id': 17,...   
26489            1.0  [{'id': 3562, 'sport_id': 1, 'country_id': 17,...   
26490            1.0  [{'id': 690, 'sport_id': 1, 'country_id': 17, ...   
18               1.0  [{'id': 690, 'sport_id': 1, 'country_id': 17, ...   
32               1.0  [{'id': 79, 'sport_id': 1, 'country_id': 17, '...   
26491            1.0  [{'id': 79, 'sport_id': 1, 'country_id': 17, '...   
26492            1.0  [{'id': 289, 'sport_id': 1, 'country_id': 17, ...   
1                1.0  [{'id': 289, 'sport_id': 1, 'country_id': 17, ...   

                                              statistics  \
26488  [{'id': 8869136, 'fixture_id': 10330189, 'type...   
17     [{'id': 8869136, 'fixture_id': 10330189, 'type...   
36     [{'id': 3786678, 'fixture_id': 10330190, 'type...   
26489  [{'id': 3786678, 'fixture_id': 10330190, 'type...   
26490  [{'id': 8869029, 'fixture_id': 10330191, 'type...   
18     [{'id': 8869029, 'fixture_id': 10330191, 'type...   
32     [{'id': 3786668, 'fixture_id': 10330192, 'type...   
26491  [{'id': 3786668, 'fixture_id': 10330192, 'type...   
26492  [{'id': 9914215, 'fixture_id': 10330193, 'type...   
1      [{'id': 9914215, 'fixture_id': 10330193, 'type...   

                                                  events clouds feels_like  \
26488  [{'id': 32406443, 'fixture_id': 10330189, 'per...    NaN        NaN   
17     [{'id': 32406443, 'fixture_id': 10330189, 'per...    NaN        NaN   
36     [{'id': 32406489, 'fixture_id': 10330190, 'per...    NaN        NaN   
26489  [{'id': 32406489, 'fixture_id': 10330190, 'per...    NaN        NaN   
26490  [{'id': 32406252, 'fixture_id': 10330191, 'per...    NaN        NaN   
18     [{'id': 32406252, 'fixture_id': 10330191, 'per...    NaN        NaN   
32     [{'id': 32406490, 'fixture_id': 10330192, 'per...    NaN        NaN   
26491  [{'id': 32406490, 'fixture_id': 10330192, 'per...    NaN        NaN   
26492  [{'id': 32406366, 'fixture_id': 10330193, 'per...    NaN        NaN   
1      [{'id': 32406366, 'fixture_id': 10330193, 'per...    NaN        NaN   

      humidity temperature  win

In [62]:
df_processed.tail(10)

fixture_id   League season  season_id  round                date  \
26404    19168033  Serie B  24-25      23839   38.0 2025-05-09 18:30:00   
52971    19168033  Serie B  24-25      23839   38.0 2025-05-09 18:30:00   
26405    19168034  Serie B  24-25      23839   38.0 2025-05-09 18:30:00   
52972    19168034  Serie B  24-25      23839   38.0 2025-05-09 18:30:00   
26406    19168035  Serie B  24-25      23839   38.0 2025-05-09 18:30:00   
52973    19168035  Serie B  24-25      23839   38.0 2025-05-09 18:30:00   
26407    19168036  Serie B  24-25      23839   38.0 2025-05-09 18:30:00   
52974    19168036  Serie B  24-25      23839   38.0 2025-05-09 18:30:00   
26402    19168037  Serie B  24-25      23839   38.0 2025-05-09 18:30:00   
52975    19168037  Serie B  24-25      23839   38.0 2025-05-09 18:30:00   

       month  day_of_week side    main_team  ... main_team_rk  rival_team_rk  \
26404     10            5    H      Palermo  ...          7.0           11.0   
52971     10            5    A    Frosinone  ...         11.0            7.0   
26405     10            5    H         Pisa  ...          2.0            9.0   
52972     10            5    A     Südtirol  ...          9.0            2.0   
26406     10            5    H    Sampdoria  ...         13.0           12.0   
52973     10            5    A  Salernitana  ...         12.0           13.0   
26407     10            5    H     Sassuolo  ...          1.0            6.0   
52974     10            5    A    Catanzaro  ...          6.0            1.0   
26402     10            5    H       Spezia  ...          3.0            4.0   
52975     10            5    A    Cremonese  ...          4.0            3.0   

                                            participants  \
26404  [{'id': 1216, 'sport_id': 1, 'country_id': 251...   
52971  [{'id': 1216, 'sport_id': 1, 'country_id': 251...   
26405  [{'id': 1072, 'sport_id': 1, 'country_id': 251...   
52972  [{'id': 1072, 'sport_id': 1, 'country_id': 251...   
26406  [{'id': 7743, 'sport_id': 1, 'country_id': 251...   
52973  [{'id': 7743, 'sport_id': 1, 'country_id': 251...   
26407  [{'id': 2714, 'sport_id': 1, 'country_id': 251...   
52974  [{'id': 2714, 'sport_id': 1, 'country_id': 251...   
26402  [{'id': 345, 'sport_id': 1, 'country_id': 251,...   
52975  [{'id': 345, 'sport_id': 1, 'country_id': 251,...   

                                              statistics  \
26404  [{'id': 386869089, 'fixture_id': 19168033, 'ty...   
52971  [{'id': 386869089, 'fixture_id': 19168033, 'ty...   
26405  [{'id': 386869699, 'fixture_id': 19168034, 'ty...   
52972  [{'id': 386869699, 'fixture_id': 19168034, 'ty...   
26406  [{'id': 386869717, 'fixture_id': 19168035, 'ty...   
52973  [{'id': 386869717, 'fixture_id': 19168035, 'ty...   
26407  [{'id': 386869087, 'fixture_id': 19168036, 'ty...   
52974  [{'id': 386869087, 'fixture_id': 19168036, 'ty...   
26402  [{'id': 386869701, 'fixture_id': 19168037, 'ty...   
52975  [{'id': 386869701, 'fixture_id': 19168037, 'ty...   

                                                  events clouds feels_like  \
26404  [{'id': 150028721, 'fixture_id': 19168033, 'pe...    NaN        NaN   
52971  [{'id': 150028721, 'fixture_id': 19168033, 'pe...    NaN        NaN   
26405  [{'id': 150028532, 'fixture_id': 19168034, 'pe...   52.0      16.20   
52972  [{'id': 150028532, 'fixture_id': 19168034, 'pe...   52.0      16.20   
26406  [{'id': 150028969, 'fixture_id': 19168035, 'pe...   84.0      19.37   
52973  [{'id': 150028969, 'fixture_id': 19168035, 'pe...   84.0      19.37   
26407  [{'id': 150029899, 'fixture_id': 19168036, 'pe...   70.0      16.19   
52974  [{'id': 150029899, 'fixture_id': 19168036, 'pe...   70.0      16.19   
26402  [{'id': 150028319, 'fixture_id': 19168037, 'pe...   18.0      16.64   
52975  [{'id': 150028319, 'fixture_id': 19168037, 'pe...   18.0      16.64   

      humidity temperature  wind_speed  
26404      NaN         NaN         NaN  
52971      NaN         NaN         Na

## Dropping rows
Remove the first 2 rounds, and the last 2 rounds of each league (taking into account that some leagues have 34 rounds.) 

In [63]:
df_processed = df_processed[(df_processed["round"]>2) & (df_processed["round"]<=34)]

#We remove the round 33 and 34 for the leagues: "Ligue 1", "Eredivisie", "Primeira Liga" and "Bundesliga":
df_processed = df_processed[~((df_processed["League"].isin(["Ligue 1", "Eredivisie", "Primeira Liga", "Bundesliga","Pro League (Belgium)"])) & (df_processed["round"].isin([33,34])))]

In [64]:
df_processed[df_processed["League"]=="La Liga"]["round"].unique().max()

34.0

In [65]:
df_processed[(df_processed["side"]=="H")]["main_team_formation"].value_counts()/len(df_processed[(df_processed["side"]=="H")])*100

main_team_formation
4-2-3-1    30.170932
4-3-3      20.113955
4-4-2      15.958217
3-5-2      14.393597
3-4-3      12.277290
5-4-1       7.086009
Name: count, dtype: float64

In [66]:
df_processed[(df_processed["side"]=="A")]["main_team_formation"].value_counts()/len(df_processed[(df_processed["side"]=="A")])*100

main_team_formation
4-2-3-1    28.674143
4-3-3      19.738627
3-5-2      15.524102
4-4-2      15.275391
3-4-3      12.675228
5-4-1       8.112508
Name: count, dtype: float64

## Export Dataset to start the 1st modeling

In [67]:
df_processed.to_csv("full_data.csv", index=False)

In [68]:
df_processed.columns

Index(['fixture_id', 'League', 'season', 'season_id', 'round', 'date', 'month',
       'day_of_week', 'side', 'main_team', 'rival_team', 'winner',
       'goals_diff', 'main_team_formation', 'rival_team_formation',
       'main_team_lineup', 'rival_team_lineup', 'main_team_bench',
       'rival_team_bench', 'main_team_acc_possession',
       'rival_team_acc_possession', 'main_team_acc_goals',
       'rival_team_acc_goals', 'main_team_acc_corners',
       'rival_team_acc_corners', 'main_team_acc_yellow_cards',
       'rival_team_acc_yellow_cards', 'main_team_acc_red_cards',
       'rival_team_acc_red_cards', 'main_team_acc_pointsL',
       'main_team_acc_pointsA', 'main_team_acc_points',
       'rival_team_acc_pointsL', 'rival_team_acc_pointsA',
       'rival_team_acc_points', 'main_team_plays_CL', 'rival_team_plays_CL',
       'main_team_rk', 'rival_team_rk', 'participants', 'statistics', 'events',
       'clouds', 'feels_like', 'humidity', 'temperature', 'wind_speed'],
      dtype='ob

In [69]:
df_processed["main_team_acc_pointsL"].mean(), df_processed["rival_team_acc_pointsL"].mean()

(0.5154818600645938, 0.5154818600645938)

In [70]:
df_processed["main_team_acc_pointsA"].mean(), df_processed["rival_team_acc_pointsA"].mean()

(0.3930974690974344, 0.3930974690974344)